In [2]:
import os
import pandas as pd
import sklearn as sk
import  psycopg2
from datetime import datetime
from dateutil.relativedelta import relativedelta
from tqdm import tqdm
import time
import warnings
import getpass
import numpy as np
import seaborn as sns
import joblib
import matplotlib.pyplot as plt 
import statsmodels.api as sm
from scipy.optimize import minimize
import pyreadr
pd.set_option('display.max_columns', 50)
import redshift_connector
from sqlalchemy import create_engine
import plotly.express as px

from pandas.tseries.offsets import MonthEnd

In [37]:
pd_data = pd.read_parquet('pit_backfill_scores_20250902.parquet')

In [55]:
pd_data[pd_data['user_id']=='7d87cbfd-c98f-4da5-8544-3224f99b3443']

user_id instrument_id  \
1400116  7d87cbfd-c98f-4da5-8544-3224f99b3443          None   

        credit_creation_date        product_flag tnc_country        pd  \
1400116           2022-05-14  Arranged Overdraft         DEU  0.023063   

         rating_class  calibration_alpha  calibration_beta  pd_wo_smoothing  \
1400116            10                1.0         -0.197961              NaN   

         rating_class_wo_smoothing  calibration_alpha_wo_smoothing  \
1400116                        NaN                             NaN   

         calibration_beta_wo_smoothing               model_name model_version  \
1400116                            NaN  supermodel-pit-20250902           1.0   

           created credit_creation_date_cohort  
1400116 2025-09-08                     2022-05

In [54]:
pd_data[pd_data['product_flag']=='Arranged Overdraft']

user_id instrument_id  \
4218     c24531fc-782b-457b-9365-e68a4c45db4c          None   
4219     68e2aff2-870e-4bde-ba09-6976c1cbe5c8          None   
4220     af99e832-d69b-45cb-bcbe-bbaf99a8c250          None   
4221     8d4d70d7-2e10-4ac8-a5e7-f6f62aca41a6          None   
4222     e938f961-7d5f-4278-8e40-69536d75407e          None   
...                                       ...           ...   
2904095  ab46f387-0a7e-480b-92c9-cf0a3b7db581          None   
2904096  282c31b1-73a3-400a-838f-8ef4e8ed9a01          None   
2904097  064398c2-d01d-468e-8bcf-4a7c408d1bcd          None   
2904098  608c82d3-c080-4158-b20b-7c2709bf17f0          None   
2904099  d0018007-acaa-4a8c-8f8f-eee5820e568a          None   

        credit_creation_date        product_flag tnc_country        pd  \
4218              2019-01-24  Arranged Overdraft         GBR  0.070389   
4219              2019-01-29  Arranged Overdraft         GBR  0.062932   
4220              2019-01-25  Arranged Overdraft         GBR  0.069630   
4221              2019-01-28  Arranged Overdraft        None  0.148381   
4222              2019-01-26  Arranged Overdraft        None  0.164271   
...                      ...                 ...         ...       ...   
2904095           2025-04-16  Arranged Overdraft         DEU  0.036253   
2904096           2025-06-14  Arranged Overdraft         DEU  0.024509   
2904097           2025-04-25  Arranged Overdraft         DEU  0.015613   
2904098           2025-05-12  Arranged Overdraft         DEU  0.016084   
2904099           2025-07-15  Arranged Overdraft         DEU  0.028342   

         rating_class  calibration_alpha  calibration_beta  pd_wo_smoothing  \
4218               13                1.0         -0.197961              NaN   
4219               13                1.0         -0.197961              NaN   
4220               13                1.0         -0.197961              NaN   
4221               14                1.0         -0.197961              NaN   
4222               14                1.0         -0.197961              NaN   
...               ...                ...               ...              ...   
2904095            11                1.0         -0.197961              NaN   
2904096            10                1.0         -0.197961              NaN   
2904097             9                1.0         -0.197961              NaN   
2904098             9                1.0         -0.197961              NaN   
2904099            10                1.0         -0.197961              NaN   

         rating_class_wo_smoothing  calibration_alpha_wo_smoothing  \
4218                           NaN                             NaN   
4219                           NaN                             NaN   
4220                           NaN                             NaN   
4221                           NaN                             NaN   
4222                           NaN                             NaN   
...                            ...                             ...   
2904095                        NaN                             NaN   
2904096                        NaN                             NaN   
2904097                        NaN                             NaN   
2904098                        NaN                             NaN   
2904099                        NaN                             NaN   

         calibration_beta_wo_smoothing               model_name model_version  \
4218                               NaN  supermodel-pit-20250902           1.0   
4219                               NaN  supermodel-pit-20250902           1.0   
4220                               NaN  supermodel-pit-20250902           1.0   
4221                               NaN  supermodel-pit-20250902           1.0   
4222                               NaN  supermodel-pit-20250902           1.0   
...                                ...                      ...           ...   
2904095                            

In [53]:
pd_data[((pd_data['credit_creation_date']==pd_data['credit_creation_date'].max()) & (pd_data['product_flag']=='Arranged Overdraft'))]

user_id instrument_id  \
2475696  a885ac68-77dc-452e-b7ad-956234c368f2          None   
2514572  cb40ab9a-50af-494b-9b1b-621542f0d6e9          None   
2514617  833177c5-1243-4db3-80a4-d7b88cdb9694          None   
2521994  4af85141-798a-4451-8b95-a033448171ec          None   
2551502  d6e55e83-bf69-4b98-8193-8c90eb0c6d8e          None   
...                                       ...           ...   
2899481  f2f86d14-c8d3-471c-ae13-6595d1db07bb          None   
2900876  e5d4ffa2-bdc9-48a6-a16a-d0ddfe148dd0          None   
2900931  06587f51-176f-4d84-89c6-a20968589c58          None   
2900941  696b5107-5e2f-4e20-a3cd-6bbf66a41065          None   
2904047  ccd6a502-f396-429b-8ba5-72d164637df9          None   

        credit_creation_date        product_flag tnc_country        pd  \
2475696           2025-08-31  Arranged Overdraft         DEU  0.028141   
2514572           2025-08-31  Arranged Overdraft         AUT  0.026838   
2514617           2025-08-31  Arranged Overdraft         AUT  0.005593   
2521994           2025-08-31  Arranged Overdraft         DEU  0.003754   
2551502           2025-08-31  Arranged Overdraft         DEU  0.016113   
...                      ...                 ...         ...       ...   
2899481           2025-08-31  Arranged Overdraft         DEU  0.007965   
2900876           2025-08-31  Arranged Overdraft         DEU  0.012196   
2900931           2025-08-31  Arranged Overdraft         DEU  0.019357   
2900941           2025-08-31  Arranged Overdraft         DEU  0.035289   
2904047           2025-08-31  Arranged Overdraft         DEU  0.024478   

         rating_class  calibration_alpha  calibration_beta  pd_wo_smoothing  \
2475696            10                1.0          1.151851              NaN   
2514572            10                1.0         -0.227762              NaN   
2514617             7                1.0         -0.227762              NaN   
2521994             6                1.0         -0.197961              NaN   
2551502             9                1.0         -0.197961              NaN   
...               ...                ...               ...              ...   
2899481             8                1.0         -0.197961              NaN   
2900876             8                1.0         -0.197961              NaN   
2900931             9                1.0         -0.197961              NaN   
2900941            11                1.0         -0.197961              NaN   
2904047            10                1.0          1.151851              NaN   

         rating_class_wo_smoothing  calibration_alpha_wo_smoothing  \
2475696                        NaN                             NaN   
2514572                        NaN                             NaN   
2514617                        NaN                             NaN   
2521994                        NaN                             NaN   
2551502                        NaN                             NaN   
...                            ...                             ...   
2899481                        NaN                             NaN   
2900876                        NaN                             NaN   
2900931                        NaN                             NaN   
2900941                        NaN                             NaN   
2904047                        NaN                             NaN   

         calibration_beta_wo_smoothing               model_name model_version  \
2475696                            NaN  supermodel-pit-20250902           1.0   
2514572                            NaN  supermodel-pit-20250902           1.0   
2514617                            NaN  supermodel-pit-20250902           1.0   
2521994                            NaN  supermodel-pit-20250902           1.0   
2551502                            NaN  supermodel-pit-20250902           1.0   
...                                ...                      ...           ...   
2899481                            

In [36]:
pd_data.groupby(['new_pit_segment'])['new_pit_beta'].mean()

new_pit_segment
AUT_OD_WITHOUT_UTILIZATION    -1.218263
AUT_OD_WITH_UTILIZATION       -0.227762
DEU_CC                        -0.639250
DEU_MIX_WITHOUT_UTILIZATION   -0.151521
DEU_MIX_WITH_UTILIZATION       1.151851
DEU_OD_WITHOUT_UTILIZATION    -1.042866
DEU_OD_WITH_UTILIZATION       -0.197961
DEU_TBIL                       0.144261
ESP_TBIL                      -0.179664
FRA_TBIL                       0.560843
ITA_TBIL                      -0.174885
UNARRANGED_OD                       NaN
Name: new_pit_beta, dtype: float64

In [2]:
password = getpass.getpass('Password: ')

In [3]:
conn = psycopg2.connect(dbname='n26'
                       , host = 'n26-dwh.cfxsmcyyfcch.eu-central-1.redshift.amazonaws.com'
                       , port = '5439'
                       , user= 'ilya_katliarou_reader'
                       , password= password
                       )

In [16]:
st = time.time()

query = f"""
with loans as (select 
m.encoded_key
, mum.user_id
, mp.product
, m.loan_amount
, max(m.creation_date::date)::date as creation_date
from  mmbr_loan_account m 
inner join dbt.mmbr_user_match mum on mum.mmbr_client_key = m.account_holder_key
inner join dbt.mmbr_loan_product_mapping mp on m.loan_name = mp.loan_name and mp.product in ('consumer_credit')
where m.creation_date::date >= '2024-01-01'::date and m.creation_date::date <= '2025-01-31'
group by 1, 2, 3, 4
)

, madrid as (
select initiator_user_id as user_id, transaction_id, transaction_amount, created::timestamp
from public.madrid_categorization
where detailed_category = 'Expenses:Leisure:Gambling'
and transaction_type not in ('TRANSACTION_TYPE_AA', 'TRANSACTION_TYPE_AR')
UNION
select user_id, transaction_id, transaction_amount, mc.created::timestamp
from public.madrid_categorization_backfill mc
inner join public.carbonium_user_account ua on mc.account_id = ua.account_id
where detailed_category = 'Expenses:Leisure:Gambling'
and transaction_type not in ('TRANSACTION_TYPE_AA', 'TRANSACTION_TYPE_AR')
)

select cd.user_id, cd.encoded_key, cd.creation_date, cd.loan_amount, m.created::timestamp, m.transaction_id, m.transaction_amount
from loans cd
left join madrid m on cd.user_id = m.user_id
"""

data = pd.read_sql_query(query, conn)
et = time.time()
elapsed_time = et - st
print('Execution time:', elapsed_time/60, 'minutes')

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/3184104277.py:35: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  data = pd.read_sql_query(query, conn)


Execution time: 0.9374572992324829 minutes


In [17]:
data

user_id  \
0       83ccdb07-f6dc-4307-beb2-fb065833c36d   
1       682ae687-9e54-4df2-8011-3621aa102677   
2       c619ba80-6486-4b02-812c-47e4f6789f23   
3       6323a6b7-36f4-497b-872c-a81304e63cea   
4       1955b37f-09b7-414c-a884-a37ad90b3755   
...                                      ...   
270021  6ae41209-908b-453b-9537-0ae65b3fb3ae   
270022  fd242f0c-eeda-4d1a-b0e7-feaee9afd54f   
270023  b2c77e63-4b6c-4ffc-a368-b42a20307c53   
270024  508f9a6a-d471-4a52-bae0-38347e190887   
270025  e72d32db-680c-417a-94f4-c6ae54f5ca8e   

                             encoded_key creation_date  loan_amount  \
0       8a868e079032532001904b8775382b7b    2024-06-24      10000.0   
1       8a868eb7924067ac0192497d9868209a    2024-10-01      25000.0   
2       8a868e56931c67f601934acb758d72d6    2024-11-20       5200.0   
3       8a868f44910644540191151268e13e19    2024-08-02       8000.0   
4       8a868ff094429207019444c2730f12c3    2025-01-08       2000.0   
...                                  ...           ...          ...   
270021  8a868ff094429207019442e833495c1d    2025-01-07      10000.0   
270022  8a868e958e2f103e018e3353d1507aaa    2024-03-12       3500.0   
270023  8a868e0a9389ee160193e8a9d48c191f    2024-12-21      15000.0   
270024  8a868ee69442919b019449428e691012    2025-01-09       1000.0   
270025  8a868e0d90dff2ba0190e04c968a741b    2024-07-23       5000.0   

                          created                        transaction_id  \
0      2023-09-04 17:14:10.447294  38ad6741-8ecf-4dc4-99a4-52d1893de667   
1      2022-04-19 20:38:32.573881  11ad37d5-dcd1-49c4-a00c-853401c388b5   
2      2021-06-16 16:11:39.524868  cb8bfeed-15ac-4e1d-b4d1-68d3acd37024   
3      2025-08-02 03:17:38.688267  b19a406f-21fb-3728-a46c-f86ee25578db   
4      2025-04-23 16:45:30.427606  a856bb69-f040-4683-b8f3-7e915fc0ebad   
...                           ...                                   ...   
270021                        NaT                                  None   
270022                        NaT                                  None   
270023                        NaT                                  None   
270024                        NaT                                  None   
270025                        NaT                                  None   

        transaction_amount  
0                    -4.50  
1                   -10.44  
2                    -1.00  
3                   -10.00  
4                   -11.00  
...                    ...  
270021                 NaN  
270022                 NaN  
270023                 NaN  
270024                 NaN  
270025                 NaN  

[270026 rows x 7 columns]

In [18]:
data['created'] = pd.to_datetime(data['created'], utc=True).dt.tz_localize(None)
data['creation_date'] = pd.to_datetime(data['creation_date'], utc=True).dt.tz_localize(None)
data['transaction_amount'] = data['transaction_amount'].abs()

In [19]:
data['user_id'].nunique()

9581

In [20]:
data['loan_amount'].sum()

1587943253.3800004

In [21]:
no_gambling_loans = data[data['transaction_id'].isna()]
gambling_loans = data[~(data['transaction_id'].isna())]

In [22]:
gambling_loans['user_id'].nunique()

4080

In [23]:
gambling_loans['before_cd'] = gambling_loans['created'] < gambling_loans['creation_date']
gambling_loans['after_cd'] = gambling_loans['created'] >= gambling_loans['creation_date']

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/2772012749.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gambling_loans['before_cd'] = gambling_loans['created'] < gambling_loans['creation_date']
/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/2772012749.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gambling_loans['after_cd'] = gambling_loans['created'] >= gambling_loans['creation_date']


In [24]:
gambling_loans

user_id  \
0       83ccdb07-f6dc-4307-beb2-fb065833c36d   
1       682ae687-9e54-4df2-8011-3621aa102677   
2       c619ba80-6486-4b02-812c-47e4f6789f23   
3       6323a6b7-36f4-497b-872c-a81304e63cea   
4       1955b37f-09b7-414c-a884-a37ad90b3755   
...                                      ...   
269988  44a1516d-47b2-4f66-ac1f-df1d154392af   
269989  dda1c66c-d3de-405c-ab8c-06fae94b6519   
269990  dda1c66c-d3de-405c-ab8c-06fae94b6519   
269991  aa64c50a-aaef-4e77-ae78-9bb0be662218   
269992  44d650f2-89a1-409b-8a27-2cc166460e63   

                             encoded_key creation_date  loan_amount  \
0       8a868e079032532001904b8775382b7b    2024-06-24      10000.0   
1       8a868eb7924067ac0192497d9868209a    2024-10-01      25000.0   
2       8a868e56931c67f601934acb758d72d6    2024-11-20       5200.0   
3       8a868f44910644540191151268e13e19    2024-08-02       8000.0   
4       8a868ff094429207019444c2730f12c3    2025-01-08       2000.0   
...                                  ...           ...          ...   
269988  8a868f40920c1a7d0192220b8f1d7bbb    2024-09-24       1500.0   
269989  8a868e01949502e70194a4d426c17b56    2025-01-26      12000.0   
269990  8a868e01949502e70194a4d426c17b56    2025-01-26      12000.0   
269991  8a868ea69389f73d0193af53269742c8    2024-12-10       1500.0   
269992  8a868e558f98f1f7018f9c1d4f451f5f    2024-05-21       1000.0   

                          created                        transaction_id  \
0      2023-09-04 17:14:10.447294  38ad6741-8ecf-4dc4-99a4-52d1893de667   
1      2022-04-19 20:38:32.573881  11ad37d5-dcd1-49c4-a00c-853401c388b5   
2      2021-06-16 16:11:39.524868  cb8bfeed-15ac-4e1d-b4d1-68d3acd37024   
3      2025-08-02 03:17:38.688267  b19a406f-21fb-3728-a46c-f86ee25578db   
4      2025-04-23 16:45:30.427606  a856bb69-f040-4683-b8f3-7e915fc0ebad   
...                           ...                                   ...   
269988 2021-07-21 20:35:42.069836  efaf252a-b4a9-30c3-b658-7ed0906270b0   
269989 2020-01-16 17:07:33.707123  be4861ed-0a2f-48cd-b5e7-e352e7ebf8d8   
269990 2019-08-15 16:05:53.245097  77f51e07-6e4a-4c06-9686-13980869887a   
269991 2019-01-29 17:14:10.990657  5379fc1f-89e9-4554-8ccb-e851c092b899   
269992 2022-06-20 20:48:56.268663  5d1e2acc-3d3e-4e07-8bf2-d8a476e982ce   

        transaction_amount  before_cd  after_cd  
0                     4.50       True     False  
1                    10.44       True     False  
2                     1.00       True     False  
3                    10.00      False      True  
4                    11.00      False      True  
...                    ...        ...       ...  
269988               10.00       True     False  
269989                0.50       True     False  
269990                7.30       True     False  
269991               10.00       True     False  
269992               20.10       True     False  

[264425 rows x 9 columns]

In [25]:
def agg_fn(group):
    result = {}
    
    before = group[group['before_cd']]
    after = group[group['after_cd']]
    
    result['first_gamble_before_cd'] = before['created'].min()
    result['last_gamble_before_cd'] = before['created'].max()
    result['count_gamble_before_cd'] = before.shape[0]
    result['sum_gamble_before_cd'] = before['transaction_amount'].sum()
    result['avg_gamble_before_cd'] = before['transaction_amount'].mean()
    
    result['first_gamble_after_cd'] = after['created'].min()
    result['last_gamble_after_cd'] = after['created'].max()
    result['count_gamble_after_cd'] = after.shape[0]
    result['sum_gamble_after_cd'] = after['transaction_amount'].sum()
    result['avg_gamble_after_cd'] = before['transaction_amount'].mean()
    
    return pd.Series(result)

In [26]:
agg_df = gambling_loans.groupby(['user_id', 'encoded_key']).apply(agg_fn).reset_index()

In [27]:
agg_df

user_id                       encoded_key  \
0     003464c8-42c1-486d-ab79-5c1453e6dfb0  8a868e9b949502e00194a876df7d4df4   
1     006480f5-91db-4c3c-88b3-21a533022719  8a868fbf8dec66f9018e067fed3c00ad   
2     0065501f-4dce-462a-a502-c8e3111c2ce4  8a868fdc9175234e0191fb271e514229   
3     006dd562-7be9-4b15-a159-2e918978c2e2  8a868e9b949502e001949b4db62019bf   
4     006fe945-e002-4130-b8ac-a88934a10bcf  8a868e0a917523530191b7ecb9ff7066   
...                                    ...                               ...   
4154  ffb23e15-cea0-4378-a5d4-a6bd641ea9a7  8a868e91916c6ef10191732952e11d78   
4155  ffb962f1-b039-4227-95d9-cd3d2c4f92e1  8a868f1f944291c001945b1784d220f5   
4156  ffc0a9f2-31ac-4d49-886f-d401ecfb3661  8a868f229121e4a9019137815bd12437   
4157  ffe2719b-2a6a-4baa-a68d-9a1a82ee4007  8a868ef2931c68070193200097d11398   
4158  ffec349b-cbb4-466c-b519-13adab22cb41  8a868e379145954d019164face7148db   

         first_gamble_before_cd      last_gamble_before_cd  \
0                           NaT                        NaT   
1    2023-09-05 16:25:03.328097 2024-02-13 17:45:12.857386   
2    2020-11-19 17:04:34.929637 2020-11-19 17:04:34.929637   
3    2024-07-04 17:49:19.601852 2024-07-04 17:49:19.601852   
4    2024-08-19 16:11:50.322640 2024-08-19 16:11:50.322640   
...                         ...                        ...   
4154 2023-08-05 23:21:30.244040 2024-08-14 17:07:13.732628   
4155 2024-05-27 06:27:30.515322 2024-07-03 11:24:27.951840   
4156 2024-03-21 17:52:35.563449 2024-03-21 17:52:35.563449   
4157 2021-02-07 01:33:58.766500 2024-04-13 07:07:11.484304   
4158 2020-11-27 05:53:58.865504 2024-04-21 08:33:18.144420   

      count_gamble_before_cd  sum_gamble_before_cd  avg_gamble_before_cd  \
0                          0                  0.00                   NaN   
1                         19                 77.60              4.084211   
2                          1                  1.40              1.400000   
3                          1                  2.10              2.100000   
4                          1                 10.00             10.000000   
...                      ...                   ...                   ...   
4154                      13                375.10             28.853846   
4155                       3                 14.80              4.933333   
4156                       1                  7.40              7.400000   
4157                       5                127.50             25.500000   
4158                      14                219.31             15.665000   

          first_gamble_after_cd       last_gamble_after_cd  \
0    2025-08-26 17:23:38.415191 2025-08-26 17:27:09.463160   
1    2024-04-08 16:28:55.223410 2025-07-29 17:30:07.661816   
2    2024-12-12 17:15:23.906610 2024-12-12 17:15:23.906610   
3                           NaT                        NaT   
4    2024-10-25 20:23:12.812481 2025-08-19 17:15:47.763054   
...                         ...                        ...   
4154 2024-08-28 16:41:25.601847 2025-07-25 16:08:55.752901   
4155 2025-04-17 06:37:18.943907 2025-04-29 06:38:03.752736   
4156 2025-03-20 22:19:34.141551 2025-03-20 22:19:34.141551   
4157 2024-11-18 17:04:56.273267 2025-07-14 16:25:23.120963   
4158 2025-02-17 12:33:26.854501 2025-03-17 12:20:06.276634   

      count_gamble_after_cd  sum_gamble_after_cd  avg_gamble_after_cd  
0                         2                17.95                  NaN  
1                        26               137.96             4.084211  
2                         1                 3.80             1.400000  
3                         0                 0.00             2.100000  
4                        25               239.95            10.000000  
...                     ...                  ...                  ...  
4154                     51              1088.10            28.853846  
4155                      2                16.55             4.933333  
4156                   

In [28]:
agg_df['user_id'].nunique()

4080

In [29]:
agg_df[agg_df['user_id']=='31e723eb-9f51-4f95-ac33-79de28e9e7c0']

user_id                       encoded_key  \
810  31e723eb-9f51-4f95-ac33-79de28e9e7c0  8a868f00931c607d01933a0b8b810607   
811  31e723eb-9f51-4f95-ac33-79de28e9e7c0  8a868fbd929c469c0192ba3adff00c22   

        first_gamble_before_cd      last_gamble_before_cd  \
810 2024-05-14 18:16:31.237062 2024-05-14 18:16:33.042279   
811 2024-05-14 18:16:31.237062 2024-05-14 18:16:33.042279   

     count_gamble_before_cd  sum_gamble_before_cd  avg_gamble_before_cd  \
810                       2                447.18                223.59   
811                       2                447.18                223.59   

    first_gamble_after_cd last_gamble_after_cd  count_gamble_after_cd  \
810                   NaT                  NaT                      0   
811                   NaT                  NaT                      0   

     sum_gamble_after_cd  avg_gamble_after_cd  
810                  0.0               223.59  
811                  0.0               223.59

In [30]:
loan_dates = gambling_loans[['user_id', 'encoded_key', 'creation_date', 'loan_amount']].drop_duplicates()
final_df = pd.merge(loan_dates, agg_df, on=['user_id', 'encoded_key'], how='left')

In [31]:
final_df['gambled_6m_before'] = (
    pd.notnull(final_df['last_gamble_before_cd']) &
    (final_df['last_gamble_before_cd'] >= final_df['creation_date'] - pd.DateOffset(months=6))
)

final_df['gambled_6m_after'] = (
    pd.notnull(final_df['first_gamble_after_cd']) &
    (final_df['first_gamble_after_cd'] <= final_df['creation_date'] + pd.DateOffset(months=6))
)

def assign_group(row):
    if row['gambled_6m_before']:
        return 'group_1'
    else:
        return 'group_2'

final_df['group'] = final_df.apply(assign_group, axis=1)

In [32]:
final_df

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
4154  bdf44b3a-28a9-4842-933f-01a723bc2966  8a868e13920c1a78019213c4fc6640a7   
4155  02db6500-6510-455f-ada7-0ef8ee357893  8a868e8a8da7de73018db1ed84261ec9   
4156  9cc34ea9-7ec1-4da3-82ea-7aaa2cf99335  8a868fbc9442919c01944ca291741856   
4157  4cd111bb-c1e6-4332-95f6-0daeba58819b  8a868ed090325339019067d978ae6ca4   
4158  460ffb1b-9cb2-447d-99f8-45901510d9db  8a868f9992fbb45f0193088dfe640a2b   

     creation_date  loan_amount     first_gamble_before_cd  \
0       2024-06-24      10000.0 2023-09-04 17:14:07.553852   
1       2024-10-01      25000.0 2021-03-23 19:18:45.387495   
2       2024-11-20       5200.0 2021-01-22 17:09:27.664615   
3       2024-08-02       8000.0                        NaT   
4       2025-01-08       2000.0 2023-12-28 17:35:34.234032   
...            ...          ...                        ...   
4154    2024-09-21       1000.0 2023-03-22 17:36:28.653315   
4155    2024-02-16       8500.0                        NaT   
4156    2025-01-09      17000.0 2023-12-14 11:41:48.934064   
4157    2024-06-30       2400.0                        NaT   
4158    2024-11-07       2500.0                        NaT   

          last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
0    2024-01-19 17:05:25.602680                       7                151.40   
1    2024-04-15 23:48:37.539253                       9               1234.69   
2    2024-11-05 18:45:19.001744                     189                722.04   
3                           NaT                       0                  0.00   
4    2025-01-07 17:36:04.653845                     115               1362.98   
...                         ...                     ...                   ...   
4154 2023-03-22 17:36:28.653315                       1                 13.80   
4155                        NaT                       0                  0.00   
4156 2023-12-14 11:41:48.934064                       1                  2.89   
4157                        NaT                       0                  0.00   
4158                        NaT                       0                  0.00   

      avg_gamble_before_cd      first_gamble_after_cd  \
0                21.628571 2024-07-11 16:18:03.988261   
1               137.187778 2025-01-30 11:29:50.312069   
2                 3.820317 2024-11-26 17:09:15.088452   
3                      NaN 2024-10-03 01:55:17.660475   
4                11.852000 2025-01-14 17:43:23.286632   
...                    ...                        ...   
4154             13.800000                        NaT   
4155                   NaN 2024-04-08 16:38:10.010730   
4156              2.890000                        NaT   
4157                   NaN 2024-10-31 17:18:31.535462   
4158                   NaN 2025-05-03 10:50:05.251278   

           last_gamble_after_cd  count_gamble_after_cd  sum_gamble_after_cd  \
0    2025-07-30 16:42:27.699472                      3                80.30   
1    2025-01-30 11:29:50.312069                      1                89.03   
2    2025-07-04 16:44:51.681319                     12               115.40   
3    2025-08-13 11:13:21.501474                      7               190.00   
4    2025-08-26 16:52:19.528307                     67               793.09   
...                         ...                    ...                  ...   
4154                        NaT                      0                 0.00   
4155 2024-04-08 16:38:10.010730        

In [33]:
final_df[final_df['user_id']=='31e723eb-9f51-4f95-ac33-79de28e9e7c0']

user_id                       encoded_key  \
3950  31e723eb-9f51-4f95-ac33-79de28e9e7c0  8a868fbd929c469c0192ba3adff00c22   
3951  31e723eb-9f51-4f95-ac33-79de28e9e7c0  8a868f00931c607d01933a0b8b810607   

     creation_date  loan_amount     first_gamble_before_cd  \
3950    2024-10-23       5000.0 2024-05-14 18:16:31.237062   
3951    2024-11-17      13000.0 2024-05-14 18:16:31.237062   

          last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
3950 2024-05-14 18:16:33.042279                       2                447.18   
3951 2024-05-14 18:16:33.042279                       2                447.18   

      avg_gamble_before_cd first_gamble_after_cd last_gamble_after_cd  \
3950                223.59                   NaT                  NaT   
3951                223.59                   NaT                  NaT   

      count_gamble_after_cd  sum_gamble_after_cd  avg_gamble_after_cd  \
3950                      0                  0.0               223.59   
3951                      0                  0.0               223.59   

      gambled_6m_before  gambled_6m_after    group  
3950               True             False  group_1  
3951              False             False  group_2

In [34]:
final_df[((final_df['count_gamble_after_cd']!=0) & (final_df['gambled_6m_after']==True))]['user_id']

0       83ccdb07-f6dc-4307-beb2-fb065833c36d
1       682ae687-9e54-4df2-8011-3621aa102677
2       c619ba80-6486-4b02-812c-47e4f6789f23
3       6323a6b7-36f4-497b-872c-a81304e63cea
4       1955b37f-09b7-414c-a884-a37ad90b3755
                        ...                 
4149    304926d2-4cc2-4399-8774-3ae23af05d69
4151    3a8329bb-223b-4e23-8d04-84ea33b71b8f
4155    02db6500-6510-455f-ada7-0ef8ee357893
4157    4cd111bb-c1e6-4332-95f6-0daeba58819b
4158    460ffb1b-9cb2-447d-99f8-45901510d9db
Name: user_id, Length: 2360, dtype: object

In [35]:
final_df[((final_df['count_gamble_after_cd']!=0) & (final_df['gambled_6m_after']==True))]['user_id']

0       83ccdb07-f6dc-4307-beb2-fb065833c36d
1       682ae687-9e54-4df2-8011-3621aa102677
2       c619ba80-6486-4b02-812c-47e4f6789f23
3       6323a6b7-36f4-497b-872c-a81304e63cea
4       1955b37f-09b7-414c-a884-a37ad90b3755
                        ...                 
4149    304926d2-4cc2-4399-8774-3ae23af05d69
4151    3a8329bb-223b-4e23-8d04-84ea33b71b8f
4155    02db6500-6510-455f-ada7-0ef8ee357893
4157    4cd111bb-c1e6-4332-95f6-0daeba58819b
4158    460ffb1b-9cb2-447d-99f8-45901510d9db
Name: user_id, Length: 2360, dtype: object

In [36]:
final_df[final_df['count_gamble_after_cd']!=0]['user_id']

0       83ccdb07-f6dc-4307-beb2-fb065833c36d
1       682ae687-9e54-4df2-8011-3621aa102677
2       c619ba80-6486-4b02-812c-47e4f6789f23
3       6323a6b7-36f4-497b-872c-a81304e63cea
4       1955b37f-09b7-414c-a884-a37ad90b3755
                        ...                 
4149    304926d2-4cc2-4399-8774-3ae23af05d69
4151    3a8329bb-223b-4e23-8d04-84ea33b71b8f
4155    02db6500-6510-455f-ada7-0ef8ee357893
4157    4cd111bb-c1e6-4332-95f6-0daeba58819b
4158    460ffb1b-9cb2-447d-99f8-45901510d9db
Name: user_id, Length: 2864, dtype: object

In [37]:
final_df[((final_df['count_gamble_before_cd']!=0) & (final_df['count_gamble_after_cd']!=0))]['user_id']

0       83ccdb07-f6dc-4307-beb2-fb065833c36d
1       682ae687-9e54-4df2-8011-3621aa102677
2       c619ba80-6486-4b02-812c-47e4f6789f23
4       1955b37f-09b7-414c-a884-a37ad90b3755
5       1ad2a561-e035-4d35-8256-3c9209887b8a
                        ...                 
4053    29a0c202-a7ad-4ac1-8bcf-196cf5d3fb1a
4059    6febd9e4-ff00-4245-b110-45924c8b34c2
4089    4d3c77df-5b35-4239-b1dd-dfbdb4fac0a7
4100    f23fbb25-8e6b-4997-bef9-76775a8fdedc
4134    a8e6cd73-0c8a-49cd-b42b-55940cfd7091
Name: user_id, Length: 2141, dtype: object

In [38]:
final_df[final_df['user_id']=='4b5dffda-f54c-4a9f-84e4-88b505814aa3']

user_id                       encoded_key  \
56  4b5dffda-f54c-4a9f-84e4-88b505814aa3  8a868e3e9494fc460194ae2b51c24167   

   creation_date  loan_amount     first_gamble_before_cd  \
56    2025-01-28       1500.0 2024-12-02 20:00:59.867008   

        last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
56 2025-01-10 17:22:34.733657                       4                  55.9   

    avg_gamble_before_cd first_gamble_after_cd last_gamble_after_cd  \
56                13.975                   NaT                  NaT   

    count_gamble_after_cd  sum_gamble_after_cd  avg_gamble_after_cd  \
56                      0                  0.0               13.975   

    gambled_6m_before  gambled_6m_after    group  
56               True             False  group_1

In [39]:
final_df['total_gamble_amount'] = final_df['sum_gamble_before_cd'] + final_df['sum_gamble_after_cd']
final_df['total_gamble_transactions'] = final_df['count_gamble_before_cd'] + final_df['count_gamble_after_cd']

In [40]:
final_df['total_gamble_amount'].quantile([0, 0.2, 0.4, 0.6, 0.8, 1])

0.0         0.200
0.2        31.380
0.4       123.744
0.6       399.260
0.8      1416.724
1.0    173872.540
Name: total_gamble_amount, dtype: float64

In [41]:
final_df['total_gamble_transactions'].quantile([0, 0.2, 0.4, 0.6, 0.8, 1])

0.0       1.0
0.2       2.0
0.4       6.0
0.6      20.0
0.8      70.0
1.0    4968.0
Name: total_gamble_transactions, dtype: float64

In [42]:
['0-50', '51-200', '201-600', '601-2000', '2001+']
['0-2', '3-8', '9-25', '26-100', '101+']

['0-2', '3-8', '9-25', '26-100', '101+']

In [43]:
amount_bins = [0, 50, 200, 600, 2000, float('inf')]
amount_labels = ['0-50', '51-200', '201-600', '601-2000', '2001+']

final_df['gambling_amount_bucket'] = pd.cut(
    final_df['total_gamble_amount'].fillna(0),
    bins=amount_bins,
    labels=amount_labels,
    include_lowest=True
)

In [44]:
freq_bins = [0, 2, 8, 25, 80, float('inf')]
freq_labels = ['0-2', '3-8', '8-25', '26-100', '101+']

final_df['gambling_freq_bucket'] = pd.cut(
    final_df['total_gamble_transactions'].fillna(0),
    bins=freq_bins,
    labels=freq_labels,
    include_lowest=True
)

In [45]:
final_df

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
4154  bdf44b3a-28a9-4842-933f-01a723bc2966  8a868e13920c1a78019213c4fc6640a7   
4155  02db6500-6510-455f-ada7-0ef8ee357893  8a868e8a8da7de73018db1ed84261ec9   
4156  9cc34ea9-7ec1-4da3-82ea-7aaa2cf99335  8a868fbc9442919c01944ca291741856   
4157  4cd111bb-c1e6-4332-95f6-0daeba58819b  8a868ed090325339019067d978ae6ca4   
4158  460ffb1b-9cb2-447d-99f8-45901510d9db  8a868f9992fbb45f0193088dfe640a2b   

     creation_date  loan_amount     first_gamble_before_cd  \
0       2024-06-24      10000.0 2023-09-04 17:14:07.553852   
1       2024-10-01      25000.0 2021-03-23 19:18:45.387495   
2       2024-11-20       5200.0 2021-01-22 17:09:27.664615   
3       2024-08-02       8000.0                        NaT   
4       2025-01-08       2000.0 2023-12-28 17:35:34.234032   
...            ...          ...                        ...   
4154    2024-09-21       1000.0 2023-03-22 17:36:28.653315   
4155    2024-02-16       8500.0                        NaT   
4156    2025-01-09      17000.0 2023-12-14 11:41:48.934064   
4157    2024-06-30       2400.0                        NaT   
4158    2024-11-07       2500.0                        NaT   

          last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
0    2024-01-19 17:05:25.602680                       7                151.40   
1    2024-04-15 23:48:37.539253                       9               1234.69   
2    2024-11-05 18:45:19.001744                     189                722.04   
3                           NaT                       0                  0.00   
4    2025-01-07 17:36:04.653845                     115               1362.98   
...                         ...                     ...                   ...   
4154 2023-03-22 17:36:28.653315                       1                 13.80   
4155                        NaT                       0                  0.00   
4156 2023-12-14 11:41:48.934064                       1                  2.89   
4157                        NaT                       0                  0.00   
4158                        NaT                       0                  0.00   

      avg_gamble_before_cd      first_gamble_after_cd  \
0                21.628571 2024-07-11 16:18:03.988261   
1               137.187778 2025-01-30 11:29:50.312069   
2                 3.820317 2024-11-26 17:09:15.088452   
3                      NaN 2024-10-03 01:55:17.660475   
4                11.852000 2025-01-14 17:43:23.286632   
...                    ...                        ...   
4154             13.800000                        NaT   
4155                   NaN 2024-04-08 16:38:10.010730   
4156              2.890000                        NaT   
4157                   NaN 2024-10-31 17:18:31.535462   
4158                   NaN 2025-05-03 10:50:05.251278   

           last_gamble_after_cd  count_gamble_after_cd  sum_gamble_after_cd  \
0    2025-07-30 16:42:27.699472                      3                80.30   
1    2025-01-30 11:29:50.312069                      1                89.03   
2    2025-07-04 16:44:51.681319                     12               115.40   
3    2025-08-13 11:13:21.501474                      7               190.00   
4    2025-08-26 16:52:19.528307                     67               793.09   
...                         ...                    ...                  ...   
4154                        NaT                      0                 0.00   
4155 2024-04-08 16:38:10.010730        

In [46]:
st = time.time()

query = f"""
select user_id, transaction_id as encoded_key, eur_written_off, max(write_off_dt::date)::date as write_off_dt 
from dbt.write_off
where reason = 'Credit'
and write_off_dt::date >= '2024-01-01'::date
group by 1, 2, 3
"""

writeoff_data = pd.read_sql_query(query, conn)
et = time.time()
elapsed_time = et - st
print('Execution time:', elapsed_time/60, 'minutes')

Execution time: 0.0010969161987304688 minutes


/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/1438357091.py:11: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  writeoff_data = pd.read_sql_query(query, conn)


In [47]:
writeoff_data['write_off_dt'] = pd.to_datetime(writeoff_data['write_off_dt'])

In [48]:
population_loans_temp = data[['user_id', 'encoded_key', 'creation_date']].drop_duplicates()
population_wo_temp = pd.merge(population_loans_temp, writeoff_data, how='left')
population_wo_temp['creation_date_eom'] = population_wo_temp['creation_date'] + MonthEnd(0)
population_wo_temp['write_off_dt_eom'] = population_wo_temp['write_off_dt'] + MonthEnd(0)

In [49]:
population_wo_temp

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
9755  6ae41209-908b-453b-9537-0ae65b3fb3ae  8a868ff094429207019442e833495c1d   
9756  fd242f0c-eeda-4d1a-b0e7-feaee9afd54f  8a868e958e2f103e018e3353d1507aaa   
9757  b2c77e63-4b6c-4ffc-a368-b42a20307c53  8a868e0a9389ee160193e8a9d48c191f   
9758  508f9a6a-d471-4a52-bae0-38347e190887  8a868ee69442919b019449428e691012   
9759  e72d32db-680c-417a-94f4-c6ae54f5ca8e  8a868e0d90dff2ba0190e04c968a741b   

     creation_date  eur_written_off write_off_dt creation_date_eom  \
0       2024-06-24              NaN          NaT        2024-06-30   
1       2024-10-01              NaN          NaT        2024-10-31   
2       2024-11-20              NaN          NaT        2024-11-30   
3       2024-08-02              NaN          NaT        2024-08-31   
4       2025-01-08              NaN          NaT        2025-01-31   
...            ...              ...          ...               ...   
9755    2025-01-07              NaN          NaT        2025-01-31   
9756    2024-03-12              NaN          NaT        2024-03-31   
9757    2024-12-21              NaN          NaT        2024-12-31   
9758    2025-01-09              NaN          NaT        2025-01-31   
9759    2024-07-23              NaN          NaT        2024-07-31   

     write_off_dt_eom  
0                 NaT  
1                 NaT  
2                 NaT  
3                 NaT  
4                 NaT  
...               ...  
9755              NaT  
9756              NaT  
9757              NaT  
9758              NaT  
9759              NaT  

[9760 rows x 7 columns]

In [50]:
population_loans_temp = data[['user_id', 'encoded_key', 'creation_date']].drop_duplicates()
population_wo_temp = pd.merge(population_loans_temp, writeoff_data, how='left')
population_wo_temp['creation_date_eom'] = population_wo_temp['creation_date'] + MonthEnd(0)
population_wo_temp['write_off_dt_eom'] = population_wo_temp['write_off_dt'] + MonthEnd(0)
population_wo_temp['writeoff_within_6m'] = (
    (population_wo_temp['write_off_dt_eom'] >= population_wo_temp['creation_date_eom']) &
    (population_wo_temp['write_off_dt_eom'] <= population_wo_temp['creation_date_eom'] + pd.DateOffset(months=6) + pd.DateOffset(days=1))
)
population_wo_temp['eur_written_off_within_6m'] = population_wo_temp['eur_written_off'].where(
    population_wo_temp['writeoff_within_6m'], 0
)

In [51]:
population_wo_temp[population_wo_temp['writeoff_within_6m']==True]['eur_written_off_within_6m'].sum()

474139.0

In [52]:
writeoff_data['write_off_dt'] = pd.to_datetime(writeoff_data['write_off_dt'])

In [53]:
writeoff_data['eur_written_off'].sum()

2672790.0

In [54]:
merged = pd.merge(
    final_df[['user_id', 'encoded_key', 'creation_date', 'loan_amount']], 
    writeoff_data[['user_id', 'encoded_key', 'write_off_dt', 'eur_written_off']], 
    on=['user_id', 'encoded_key'], 
    how='left'
)

merged['creation_date_eom'] = merged['creation_date'] + MonthEnd(0)
merged['write_off_dt_eom'] = merged['write_off_dt'] + MonthEnd(0)

In [55]:
merged['eur_written_off'].sum()

531236.0

In [56]:
merged

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
4154  bdf44b3a-28a9-4842-933f-01a723bc2966  8a868e13920c1a78019213c4fc6640a7   
4155  02db6500-6510-455f-ada7-0ef8ee357893  8a868e8a8da7de73018db1ed84261ec9   
4156  9cc34ea9-7ec1-4da3-82ea-7aaa2cf99335  8a868fbc9442919c01944ca291741856   
4157  4cd111bb-c1e6-4332-95f6-0daeba58819b  8a868ed090325339019067d978ae6ca4   
4158  460ffb1b-9cb2-447d-99f8-45901510d9db  8a868f9992fbb45f0193088dfe640a2b   

     creation_date  loan_amount write_off_dt  eur_written_off  \
0       2024-06-24      10000.0          NaT              NaN   
1       2024-10-01      25000.0          NaT              NaN   
2       2024-11-20       5200.0          NaT              NaN   
3       2024-08-02       8000.0          NaT              NaN   
4       2025-01-08       2000.0          NaT              NaN   
...            ...          ...          ...              ...   
4154    2024-09-21       1000.0          NaT              NaN   
4155    2024-02-16       8500.0          NaT              NaN   
4156    2025-01-09      17000.0          NaT              NaN   
4157    2024-06-30       2400.0          NaT              NaN   
4158    2024-11-07       2500.0          NaT              NaN   

     creation_date_eom write_off_dt_eom  
0           2024-06-30              NaT  
1           2024-10-31              NaT  
2           2024-11-30              NaT  
3           2024-08-31              NaT  
4           2025-01-31              NaT  
...                ...              ...  
4154        2024-09-30              NaT  
4155        2024-02-29              NaT  
4156        2025-01-31              NaT  
4157        2024-06-30              NaT  
4158        2024-11-30              NaT  

[4159 rows x 8 columns]

In [57]:
merged['writeoff_within_6m'] = (
    (merged['write_off_dt_eom'] >= merged['creation_date_eom']) &
    (merged['write_off_dt_eom'] <= merged['creation_date_eom'] + pd.DateOffset(months=6) + pd.DateOffset(days=1))
)
merged['eur_written_off_within_6m'] = merged['eur_written_off'].where(
    merged['writeoff_within_6m'], 0
)
writeoff_agg = merged.groupby('user_id').agg(
    writeoff_within_6m=('writeoff_within_6m', 'any'),
    eur_written_off_within_6m=('eur_written_off_within_6m', 'sum')
).reset_index()
final_df = pd.merge(final_df, writeoff_agg, on='user_id', how='left')

In [58]:
final_df

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
4154  bdf44b3a-28a9-4842-933f-01a723bc2966  8a868e13920c1a78019213c4fc6640a7   
4155  02db6500-6510-455f-ada7-0ef8ee357893  8a868e8a8da7de73018db1ed84261ec9   
4156  9cc34ea9-7ec1-4da3-82ea-7aaa2cf99335  8a868fbc9442919c01944ca291741856   
4157  4cd111bb-c1e6-4332-95f6-0daeba58819b  8a868ed090325339019067d978ae6ca4   
4158  460ffb1b-9cb2-447d-99f8-45901510d9db  8a868f9992fbb45f0193088dfe640a2b   

     creation_date  loan_amount     first_gamble_before_cd  \
0       2024-06-24      10000.0 2023-09-04 17:14:07.553852   
1       2024-10-01      25000.0 2021-03-23 19:18:45.387495   
2       2024-11-20       5200.0 2021-01-22 17:09:27.664615   
3       2024-08-02       8000.0                        NaT   
4       2025-01-08       2000.0 2023-12-28 17:35:34.234032   
...            ...          ...                        ...   
4154    2024-09-21       1000.0 2023-03-22 17:36:28.653315   
4155    2024-02-16       8500.0                        NaT   
4156    2025-01-09      17000.0 2023-12-14 11:41:48.934064   
4157    2024-06-30       2400.0                        NaT   
4158    2024-11-07       2500.0                        NaT   

          last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
0    2024-01-19 17:05:25.602680                       7                151.40   
1    2024-04-15 23:48:37.539253                       9               1234.69   
2    2024-11-05 18:45:19.001744                     189                722.04   
3                           NaT                       0                  0.00   
4    2025-01-07 17:36:04.653845                     115               1362.98   
...                         ...                     ...                   ...   
4154 2023-03-22 17:36:28.653315                       1                 13.80   
4155                        NaT                       0                  0.00   
4156 2023-12-14 11:41:48.934064                       1                  2.89   
4157                        NaT                       0                  0.00   
4158                        NaT                       0                  0.00   

      avg_gamble_before_cd      first_gamble_after_cd  \
0                21.628571 2024-07-11 16:18:03.988261   
1               137.187778 2025-01-30 11:29:50.312069   
2                 3.820317 2024-11-26 17:09:15.088452   
3                      NaN 2024-10-03 01:55:17.660475   
4                11.852000 2025-01-14 17:43:23.286632   
...                    ...                        ...   
4154             13.800000                        NaT   
4155                   NaN 2024-04-08 16:38:10.010730   
4156              2.890000                        NaT   
4157                   NaN 2024-10-31 17:18:31.535462   
4158                   NaN 2025-05-03 10:50:05.251278   

           last_gamble_after_cd  count_gamble_after_cd  sum_gamble_after_cd  \
0    2025-07-30 16:42:27.699472                      3                80.30   
1    2025-01-30 11:29:50.312069                      1                89.03   
2    2025-07-04 16:44:51.681319                     12               115.40   
3    2025-08-13 11:13:21.501474                      7               190.00   
4    2025-08-26 16:52:19.528307                     67               793.09   
...                         ...                    ...                  ...   
4154                        NaT                      0                 0.00   
4155 2024-04-08 16:38:10.010730        

In [59]:
final_df[((final_df['count_gamble_before_cd']!=0) & (final_df['count_gamble_after_cd']!=0))]['eur_written_off_within_12m'].sum()

KeyError: 'eur_written_off_within_12m'

In [60]:
final_df['eur_written_off_within_6m'].max()

22543.0

In [61]:
st = time.time()

query = f"""
select
a.encoded_key,
sum(r.interest_paid + r.fees_paid) as revenue_eur
from mmbr_loan_account as a
inner join mmbr_repayment as r
        on r.parent_account_key = a.encoded_key
            and r.repaid_date <= last_day(date_add('month', 6, creation_date::date))
inner join dbt.mmbr_loan_product_mapping lpm
        on a.loan_name = lpm.loan_name
            and lpm.product in ('consumer_credit')
group by 1
"""

revenue_data = pd.read_sql_query(query, conn)
et = time.time()
elapsed_time = et - st
print('Execution time:', elapsed_time/60, 'minutes')

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/2369637799.py:17: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  revenue_data = pd.read_sql_query(query, conn)


Execution time: 0.21337000131607056 minutes


In [62]:
population_loans_temp = data[['user_id', 'encoded_key', 'creation_date']].drop_duplicates()
population_rvn_temp = pd.merge(population_loans_temp, revenue_data, how='left')

In [63]:
population_rvn_temp['revenue_eur'].sum()

2731591.8

In [64]:
revenue_data['revenue_eur'].sum()

6223257.57

In [65]:
final_df

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
4154  bdf44b3a-28a9-4842-933f-01a723bc2966  8a868e13920c1a78019213c4fc6640a7   
4155  02db6500-6510-455f-ada7-0ef8ee357893  8a868e8a8da7de73018db1ed84261ec9   
4156  9cc34ea9-7ec1-4da3-82ea-7aaa2cf99335  8a868fbc9442919c01944ca291741856   
4157  4cd111bb-c1e6-4332-95f6-0daeba58819b  8a868ed090325339019067d978ae6ca4   
4158  460ffb1b-9cb2-447d-99f8-45901510d9db  8a868f9992fbb45f0193088dfe640a2b   

     creation_date  loan_amount     first_gamble_before_cd  \
0       2024-06-24      10000.0 2023-09-04 17:14:07.553852   
1       2024-10-01      25000.0 2021-03-23 19:18:45.387495   
2       2024-11-20       5200.0 2021-01-22 17:09:27.664615   
3       2024-08-02       8000.0                        NaT   
4       2025-01-08       2000.0 2023-12-28 17:35:34.234032   
...            ...          ...                        ...   
4154    2024-09-21       1000.0 2023-03-22 17:36:28.653315   
4155    2024-02-16       8500.0                        NaT   
4156    2025-01-09      17000.0 2023-12-14 11:41:48.934064   
4157    2024-06-30       2400.0                        NaT   
4158    2024-11-07       2500.0                        NaT   

          last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
0    2024-01-19 17:05:25.602680                       7                151.40   
1    2024-04-15 23:48:37.539253                       9               1234.69   
2    2024-11-05 18:45:19.001744                     189                722.04   
3                           NaT                       0                  0.00   
4    2025-01-07 17:36:04.653845                     115               1362.98   
...                         ...                     ...                   ...   
4154 2023-03-22 17:36:28.653315                       1                 13.80   
4155                        NaT                       0                  0.00   
4156 2023-12-14 11:41:48.934064                       1                  2.89   
4157                        NaT                       0                  0.00   
4158                        NaT                       0                  0.00   

      avg_gamble_before_cd      first_gamble_after_cd  \
0                21.628571 2024-07-11 16:18:03.988261   
1               137.187778 2025-01-30 11:29:50.312069   
2                 3.820317 2024-11-26 17:09:15.088452   
3                      NaN 2024-10-03 01:55:17.660475   
4                11.852000 2025-01-14 17:43:23.286632   
...                    ...                        ...   
4154             13.800000                        NaT   
4155                   NaN 2024-04-08 16:38:10.010730   
4156              2.890000                        NaT   
4157                   NaN 2024-10-31 17:18:31.535462   
4158                   NaN 2025-05-03 10:50:05.251278   

           last_gamble_after_cd  count_gamble_after_cd  sum_gamble_after_cd  \
0    2025-07-30 16:42:27.699472                      3                80.30   
1    2025-01-30 11:29:50.312069                      1                89.03   
2    2025-07-04 16:44:51.681319                     12               115.40   
3    2025-08-13 11:13:21.501474                      7               190.00   
4    2025-08-26 16:52:19.528307                     67               793.09   
...                         ...                    ...                  ...   
4154                        NaT                      0                 0.00   
4155 2024-04-08 16:38:10.010730        

In [66]:
final_v1 = final_df.merge(revenue_data, on=['encoded_key'], how='left')
final_v1['revenue_eur'] = final_v1['revenue_eur'].fillna(0)

In [67]:
final_v1['eur_written_off_within_6m'] = final_v1['eur_written_off_within_6m'].fillna(0)

In [68]:
final_v1['profit_eur'] = final_v1['revenue_eur'] - final_v1['eur_written_off_within_6m']

In [69]:
final_v1[final_v1['count_gamble_after_cd']!=0]['profit_eur'].sum()

698480.62

In [70]:
final_v1['revenue_eur'].sum()

1174329.19

In [71]:
top_20 = final_v1.nlargest(30, 'eur_written_off_within_6m')

In [72]:
top_20

user_id                       encoded_key  \
1700  c943eaf4-335e-4351-adab-ed44adf35162  8a868f66931c67f801931fcf888942ba   
3797  cf437c81-5d08-4784-9251-3a9eae5ad1d2  8a868f43946bbfa701946e5a2cae2481   
2564  bfcbf174-b1a2-4e16-9270-8721016e7053  8a868eaa91b113c901920574e87a0a94   
2226  0d554d9d-d319-4c4e-b250-d7f089ae97aa  8a868e61926d62b701927b453d800fc7   
443   5213071c-8417-4bc4-8228-01cf9601ca7b  8a868f46938a01490193bbf433124bd7   
1389  757e1369-7ec9-497e-9cae-8567d58bbd10  8a868e0a9389ee160193c12950db30cd   
2044  404d4c52-4b35-44bf-bfeb-aed13b69bde0  8a868ea69389f73d0194004186ea0fef   
1749  0fbff2b3-2746-4796-b28a-7e6214e24386  8a868fb6939c63500193c45a915229d6   
4076  7e55fd40-361f-4008-a4a5-1629ddc83e8b  8a868ed9929c47580192dc9b257e17a8   
2879  16cccfe3-b035-454e-9eed-d9580eb4352a  8a868fb6939c63500193cdcd69874f15   
948   b93657f4-4389-417f-8403-02317f95d0ad  8a868f0c949502e90194bcbdbff36a28   
1690  4d60e106-f499-4e1e-b06e-059b94241068  8a868f64949502ce019499c89ece17bf   
1497  ce1a13f9-5f13-400c-8dd5-635bcb3714b7  8a868f18912bf67401915a05cea25f0d   
2284  547956dd-52b3-4498-9faf-4ebba019450b  8a868f46938a014901939678a39a2078   
2285  547956dd-52b3-4498-9faf-4ebba019450b  8a868f728ccfb11f018cd4daf9fb6753   
973   5454f3ea-9a44-4705-955a-1a528a884bd2  8a868ed9936f6bf50193846acd7a5a95   
284   249fe706-1101-4d65-999e-e9f01dd1b200  8a868e589126daab019145ffe1d372c6   
3206  8b51983c-7207-4222-97ac-b8149cf81921  8a868f28949502de0194a8266b1c6f23   
2547  0eb43dc0-7a39-4c7f-95cd-40c94bfa6e20  8a868f3e936f6afa019379f817f674a2   
1172  4fc8e5c2-8426-4e84-a1c3-833240a6f0ef  8a868f419389ed2a0193bd0bb1a20ab0   
2662  8511068e-15b9-4182-a409-5ecafdb49a24  8a868eb2946c98e701946fb9d749126a   
3870  d9c00600-69d3-42f5-99a1-89c64610044b  8a868f6b8dc345c2018deb65fee8417d   
1328  90ef291c-4a12-4e18-819d-91a7f5fd5394  8a868eeb9389ebf7019393e642e36317   
3737  0e3ccf61-eb44-4e08-8080-2c099769f8af  8a868ff8916c6f1701916f53437912d1   
2436  5cf229b9-f62f-4431-8f96-9e084a06c950  8a868e96938a0146019408ab48495b15   
27    fdb5670b-7158-47af-be45-b89d377f2ce7  8a868ec3916c6eeb01916fe7af1140b3   
3106  2c599b3c-372f-42ee-b41e-c8dcd63d44a5  8a868fb6939c63500193b0f46ecc44ea   
1864  c0f81287-7932-40ad-ac89-a3e5b3c3886d  8a868ead8e38b4b5018e39f5830c002a   
1165  998068f2-b38d-4d23-abf4-65ad91489c72  8a868ebe9175234a0191afbdc485564d   
245   bb0d4afe-cb7f-43ef-87a0-cf61b7f073ad  8a868ea5926d6e1401927275d1543c1a   

     creation_date  loan_amount     first_gamble_before_cd  \
1700    2024-11-12      25000.0 2019-10-08 16:08:48.666045   
3797    2025-01-16      20000.0 2023-12-22 21:00:16.234082   
2564    2024-09-18      20000.0 2019-08-07 08:07:29.419887   
2226    2024-10-11      10000.0 2022-09-29 20:33:18.804931   
443     2024-12-12      10000.0 2019-05-16 21:49:10.197284   
1389    2024-12-13      10000.0 2023-05-25 05:32:51.119940   
2044    2024-12-25      10000.0 2024-06-30 22:05:01.366395   
1749    2024-12-14      10000.0 2020-06-29 16:14:19.091773   
4076    2024-10-30      10000.0 2020-08-10 16:29:56.265932   
2879    2024-12-16      10000.0 2022-07-20 16:08:33.402969   
948     2025-01-31       8400.0 2023-06-09 06:07:47.557836   
1690    2025-01-24       8000.0 2024-12-31 20:22:16.972594   
1497    2024-08-16       7500.0 2023-04-03 20:54:17.051515   
2284    2024-12-05       7000.0 2023-05-19 13:37:22.354382   
2285    2024-01-04       2500.0 2023-05-19 13:37:22.354382   
973     2024-12-01       6900.0 2024-06-24 16:31:11.646609   
284     2024-08-12       7000.0 2018-07-12 11:44:00.416517   
3206    2025-01-27       6000.0 2024-09-10 21:16:10.532745   
2547    2024-11-29       5400.0 2020-04-09 02:51:57.498857   
1172    2024-12-12       5000.0 2023-05-12 08:41:30.562448   
2662    2025-01-16       5000.0 2024-05-09 22:01:52.501642   
3870    2024-02-27       4500.0                        NaT   
1328    2024-12-04       3900.0                        NaT   
3737    2024-08-20       3500.0 2024-07-04 07:12:17.660770   
2436

In [73]:
final_v1[final_v1['writeoff_within_6m']==True]

user_id                       encoded_key  \
27    fdb5670b-7158-47af-be45-b89d377f2ce7  8a868ec3916c6eeb01916fe7af1140b3   
38    c97cdb3e-4899-4266-84e5-025fb44765be  8a868e6492759d1d019299db2f7947ad   
245   bb0d4afe-cb7f-43ef-87a0-cf61b7f073ad  8a868ea5926d6e1401927275d1543c1a   
284   249fe706-1101-4d65-999e-e9f01dd1b200  8a868e589126daab019145ffe1d372c6   
405   5028f2f5-73b4-4b8e-99ae-376802275581  8a868e1992fbb45d019309b4fa3e0168   
443   5213071c-8417-4bc4-8228-01cf9601ca7b  8a868f46938a01490193bbf433124bd7   
578   c292632b-1e80-48d0-b009-cdf0a2bd340f  8a868f909067baf501906d02f7a340d2   
948   b93657f4-4389-417f-8403-02317f95d0ad  8a868f0c949502e90194bcbdbff36a28   
973   5454f3ea-9a44-4705-955a-1a528a884bd2  8a868ed9936f6bf50193846acd7a5a95   
1165  998068f2-b38d-4d23-abf4-65ad91489c72  8a868ebe9175234a0191afbdc485564d   
1172  4fc8e5c2-8426-4e84-a1c3-833240a6f0ef  8a868f419389ed2a0193bd0bb1a20ab0   
1260  7a0945d3-84d3-4b86-a90d-760a1dbb831f  8a868ed48dec6742018dfc9e7ea07fb3   
1328  90ef291c-4a12-4e18-819d-91a7f5fd5394  8a868eeb9389ebf7019393e642e36317   
1389  757e1369-7ec9-497e-9cae-8567d58bbd10  8a868e0a9389ee160193c12950db30cd   
1497  ce1a13f9-5f13-400c-8dd5-635bcb3714b7  8a868f18912bf67401915a05cea25f0d   
1690  4d60e106-f499-4e1e-b06e-059b94241068  8a868f64949502ce019499c89ece17bf   
1700  c943eaf4-335e-4351-adab-ed44adf35162  8a868f66931c67f801931fcf888942ba   
1749  0fbff2b3-2746-4796-b28a-7e6214e24386  8a868fb6939c63500193c45a915229d6   
1864  c0f81287-7932-40ad-ac89-a3e5b3c3886d  8a868ead8e38b4b5018e39f5830c002a   
2044  404d4c52-4b35-44bf-bfeb-aed13b69bde0  8a868ea69389f73d0194004186ea0fef   
2082  32f45cde-df87-49ee-9589-d303de04a262  8a868fef9175234d0191e6aaea326a2e   
2084  a618f0a0-4ab6-4a5d-88dc-2194c3ea10e7  8a868e0a9389ee16019412cbbdf170c4   
2226  0d554d9d-d319-4c4e-b250-d7f089ae97aa  8a868e61926d62b701927b453d800fc7   
2284  547956dd-52b3-4498-9faf-4ebba019450b  8a868f46938a014901939678a39a2078   
2285  547956dd-52b3-4498-9faf-4ebba019450b  8a868f728ccfb11f018cd4daf9fb6753   
2436  5cf229b9-f62f-4431-8f96-9e084a06c950  8a868e96938a0146019408ab48495b15   
2547  0eb43dc0-7a39-4c7f-95cd-40c94bfa6e20  8a868f3e936f6afa019379f817f674a2   
2564  bfcbf174-b1a2-4e16-9270-8721016e7053  8a868eaa91b113c901920574e87a0a94   
2662  8511068e-15b9-4182-a409-5ecafdb49a24  8a868eb2946c98e701946fb9d749126a   
2879  16cccfe3-b035-454e-9eed-d9580eb4352a  8a868fb6939c63500193cdcd69874f15   
3106  2c599b3c-372f-42ee-b41e-c8dcd63d44a5  8a868fb6939c63500193b0f46ecc44ea   
3206  8b51983c-7207-4222-97ac-b8149cf81921  8a868f28949502de0194a8266b1c6f23   
3543  867e435d-65e4-4435-8a4a-c206d25bd5f2  8a868fb6939c635001942bd11c897343   
3587  86059e7a-0ef5-4747-9fec-fe7e08bb9707  8a868f43946bbfa701948348e8063738   
3737  0e3ccf61-eb44-4e08-8080-2c099769f8af  8a868ff8916c6f1701916f53437912d1   
3797  cf437c81-5d08-4784-9251-3a9eae5ad1d2  8a868f43946bbfa701946e5a2cae2481   
3870  d9c00600-69d3-42f5-99a1-89c64610044b  8a868f6b8dc345c2018deb65fee8417d   
4076  7e55fd40-361f-4008-a4a5-1629ddc83e8b  8a868ed9929c47580192dc9b257e17a8   

     creation_date  loan_amount     first_gamble_before_cd  \
27      2024-08-20       3000.0 2023-02-08 21:19:19.858795   
38      2024-10-17       1500.0 2018-07-14 17:25:34.295888   
245     2024-10-09       2000.0 2020-05-31 22:37:30.984842   
284     2024-08-12       7000.0 2018-07-12 11:44:00.416517   
405     2024-11-08       1000.0 2020-11-27 05:54:12.530579   
443     2024-12-12      10000.0 2019-05-16 21:49:10.197284   
578     2024-07-01       1000.0 2023-09-08 06:32:45.029836   
948     2025-01-31       8400.0 2023-06-09 06:07:47.557836   
973     2024-12-01       6900.0 2024-06-24 16:31:11.646609   
1165    2024-09-01       2000.0 2024-05-29 16:00:18.977148   
1172    2024-12-12       5000.0 2023-05-12 08:41:30.562448   
1260    2024-03-02       1000.0 2021-02-18 15:41:12.092933   
1328    2024-12-04       3900.0                        NaT   
1389    2024-12-13      10000.0 2023-05-25 05:

In [74]:
final_v1['revenue_eur'] = final_v1['revenue_eur'].fillna(0)
final_v1['profit_eur'] = final_v1['profit_eur'].fillna(0)

In [75]:
final_v1[final_v1['writeoff_within_6m']==True]

user_id                       encoded_key  \
27    fdb5670b-7158-47af-be45-b89d377f2ce7  8a868ec3916c6eeb01916fe7af1140b3   
38    c97cdb3e-4899-4266-84e5-025fb44765be  8a868e6492759d1d019299db2f7947ad   
245   bb0d4afe-cb7f-43ef-87a0-cf61b7f073ad  8a868ea5926d6e1401927275d1543c1a   
284   249fe706-1101-4d65-999e-e9f01dd1b200  8a868e589126daab019145ffe1d372c6   
405   5028f2f5-73b4-4b8e-99ae-376802275581  8a868e1992fbb45d019309b4fa3e0168   
443   5213071c-8417-4bc4-8228-01cf9601ca7b  8a868f46938a01490193bbf433124bd7   
578   c292632b-1e80-48d0-b009-cdf0a2bd340f  8a868f909067baf501906d02f7a340d2   
948   b93657f4-4389-417f-8403-02317f95d0ad  8a868f0c949502e90194bcbdbff36a28   
973   5454f3ea-9a44-4705-955a-1a528a884bd2  8a868ed9936f6bf50193846acd7a5a95   
1165  998068f2-b38d-4d23-abf4-65ad91489c72  8a868ebe9175234a0191afbdc485564d   
1172  4fc8e5c2-8426-4e84-a1c3-833240a6f0ef  8a868f419389ed2a0193bd0bb1a20ab0   
1260  7a0945d3-84d3-4b86-a90d-760a1dbb831f  8a868ed48dec6742018dfc9e7ea07fb3   
1328  90ef291c-4a12-4e18-819d-91a7f5fd5394  8a868eeb9389ebf7019393e642e36317   
1389  757e1369-7ec9-497e-9cae-8567d58bbd10  8a868e0a9389ee160193c12950db30cd   
1497  ce1a13f9-5f13-400c-8dd5-635bcb3714b7  8a868f18912bf67401915a05cea25f0d   
1690  4d60e106-f499-4e1e-b06e-059b94241068  8a868f64949502ce019499c89ece17bf   
1700  c943eaf4-335e-4351-adab-ed44adf35162  8a868f66931c67f801931fcf888942ba   
1749  0fbff2b3-2746-4796-b28a-7e6214e24386  8a868fb6939c63500193c45a915229d6   
1864  c0f81287-7932-40ad-ac89-a3e5b3c3886d  8a868ead8e38b4b5018e39f5830c002a   
2044  404d4c52-4b35-44bf-bfeb-aed13b69bde0  8a868ea69389f73d0194004186ea0fef   
2082  32f45cde-df87-49ee-9589-d303de04a262  8a868fef9175234d0191e6aaea326a2e   
2084  a618f0a0-4ab6-4a5d-88dc-2194c3ea10e7  8a868e0a9389ee16019412cbbdf170c4   
2226  0d554d9d-d319-4c4e-b250-d7f089ae97aa  8a868e61926d62b701927b453d800fc7   
2284  547956dd-52b3-4498-9faf-4ebba019450b  8a868f46938a014901939678a39a2078   
2285  547956dd-52b3-4498-9faf-4ebba019450b  8a868f728ccfb11f018cd4daf9fb6753   
2436  5cf229b9-f62f-4431-8f96-9e084a06c950  8a868e96938a0146019408ab48495b15   
2547  0eb43dc0-7a39-4c7f-95cd-40c94bfa6e20  8a868f3e936f6afa019379f817f674a2   
2564  bfcbf174-b1a2-4e16-9270-8721016e7053  8a868eaa91b113c901920574e87a0a94   
2662  8511068e-15b9-4182-a409-5ecafdb49a24  8a868eb2946c98e701946fb9d749126a   
2879  16cccfe3-b035-454e-9eed-d9580eb4352a  8a868fb6939c63500193cdcd69874f15   
3106  2c599b3c-372f-42ee-b41e-c8dcd63d44a5  8a868fb6939c63500193b0f46ecc44ea   
3206  8b51983c-7207-4222-97ac-b8149cf81921  8a868f28949502de0194a8266b1c6f23   
3543  867e435d-65e4-4435-8a4a-c206d25bd5f2  8a868fb6939c635001942bd11c897343   
3587  86059e7a-0ef5-4747-9fec-fe7e08bb9707  8a868f43946bbfa701948348e8063738   
3737  0e3ccf61-eb44-4e08-8080-2c099769f8af  8a868ff8916c6f1701916f53437912d1   
3797  cf437c81-5d08-4784-9251-3a9eae5ad1d2  8a868f43946bbfa701946e5a2cae2481   
3870  d9c00600-69d3-42f5-99a1-89c64610044b  8a868f6b8dc345c2018deb65fee8417d   
4076  7e55fd40-361f-4008-a4a5-1629ddc83e8b  8a868ed9929c47580192dc9b257e17a8   

     creation_date  loan_amount     first_gamble_before_cd  \
27      2024-08-20       3000.0 2023-02-08 21:19:19.858795   
38      2024-10-17       1500.0 2018-07-14 17:25:34.295888   
245     2024-10-09       2000.0 2020-05-31 22:37:30.984842   
284     2024-08-12       7000.0 2018-07-12 11:44:00.416517   
405     2024-11-08       1000.0 2020-11-27 05:54:12.530579   
443     2024-12-12      10000.0 2019-05-16 21:49:10.197284   
578     2024-07-01       1000.0 2023-09-08 06:32:45.029836   
948     2025-01-31       8400.0 2023-06-09 06:07:47.557836   
973     2024-12-01       6900.0 2024-06-24 16:31:11.646609   
1165    2024-09-01       2000.0 2024-05-29 16:00:18.977148   
1172    2024-12-12       5000.0 2023-05-12 08:41:30.562448   
1260    2024-03-02       1000.0 2021-02-18 15:41:12.092933   
1328    2024-12-04       3900.0                        NaT   
1389    2024-12-13      10000.0 2023-05-25 05:

In [76]:
final_v1['RoA'] = final_v1['profit_eur'] / final_v1['loan_amount']
final_v1['WO_Rate'] = final_v1['eur_written_off_within_6m'] / final_v1['loan_amount']

In [77]:
final_v1

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
4154  bdf44b3a-28a9-4842-933f-01a723bc2966  8a868e13920c1a78019213c4fc6640a7   
4155  02db6500-6510-455f-ada7-0ef8ee357893  8a868e8a8da7de73018db1ed84261ec9   
4156  9cc34ea9-7ec1-4da3-82ea-7aaa2cf99335  8a868fbc9442919c01944ca291741856   
4157  4cd111bb-c1e6-4332-95f6-0daeba58819b  8a868ed090325339019067d978ae6ca4   
4158  460ffb1b-9cb2-447d-99f8-45901510d9db  8a868f9992fbb45f0193088dfe640a2b   

     creation_date  loan_amount     first_gamble_before_cd  \
0       2024-06-24      10000.0 2023-09-04 17:14:07.553852   
1       2024-10-01      25000.0 2021-03-23 19:18:45.387495   
2       2024-11-20       5200.0 2021-01-22 17:09:27.664615   
3       2024-08-02       8000.0                        NaT   
4       2025-01-08       2000.0 2023-12-28 17:35:34.234032   
...            ...          ...                        ...   
4154    2024-09-21       1000.0 2023-03-22 17:36:28.653315   
4155    2024-02-16       8500.0                        NaT   
4156    2025-01-09      17000.0 2023-12-14 11:41:48.934064   
4157    2024-06-30       2400.0                        NaT   
4158    2024-11-07       2500.0                        NaT   

          last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
0    2024-01-19 17:05:25.602680                       7                151.40   
1    2024-04-15 23:48:37.539253                       9               1234.69   
2    2024-11-05 18:45:19.001744                     189                722.04   
3                           NaT                       0                  0.00   
4    2025-01-07 17:36:04.653845                     115               1362.98   
...                         ...                     ...                   ...   
4154 2023-03-22 17:36:28.653315                       1                 13.80   
4155                        NaT                       0                  0.00   
4156 2023-12-14 11:41:48.934064                       1                  2.89   
4157                        NaT                       0                  0.00   
4158                        NaT                       0                  0.00   

      avg_gamble_before_cd      first_gamble_after_cd  \
0                21.628571 2024-07-11 16:18:03.988261   
1               137.187778 2025-01-30 11:29:50.312069   
2                 3.820317 2024-11-26 17:09:15.088452   
3                      NaN 2024-10-03 01:55:17.660475   
4                11.852000 2025-01-14 17:43:23.286632   
...                    ...                        ...   
4154             13.800000                        NaT   
4155                   NaN 2024-04-08 16:38:10.010730   
4156              2.890000                        NaT   
4157                   NaN 2024-10-31 17:18:31.535462   
4158                   NaN 2025-05-03 10:50:05.251278   

           last_gamble_after_cd  count_gamble_after_cd  sum_gamble_after_cd  \
0    2025-07-30 16:42:27.699472                      3                80.30   
1    2025-01-30 11:29:50.312069                      1                89.03   
2    2025-07-04 16:44:51.681319                     12               115.40   
3    2025-08-13 11:13:21.501474                      7               190.00   
4    2025-08-26 16:52:19.528307                     67               793.09   
...                         ...                    ...                  ...   
4154                        NaT                      0                 0.00   
4155 2024-04-08 16:38:10.010730        

In [78]:
st = time.time()

query = f"""

with rating_map as (
    select 'A' as rating, 1 as rating_rank union all
    select 'B', 2 union all
    select 'C', 3 union all
    select 'D', 4 union all
    select 'E', 5 union all
    select 'F', 6 union all
    select 'G', 7 union all
    select 'H', 8 union all
    select 'I', 9 union all
    select 'K', 10 union all
    select 'L', 11 union all
    select 'M', 12 union all
    select 'N', 13 union all
    select 'O', 14 union all
    select 'P', 15
),
scored as (
    select
        mum.user_id,
        c.rating,
        rm.rating_rank,
        c.purpose,
        c.requested_on::date as requested_on,
        m.creation_date::date as creation_date,
        row_number() over (
            partition by mum.user_id
            order by c.requested_on desc
        ) as rn_latest,
        row_number() over (
            partition by mum.user_id
            order by rm.rating_rank desc, c.requested_on asc
        ) as rn_worst
    from mmbr_loan_account m
    inner join dbt.mmbr_user_match mum 
        on mum.mmbr_client_key = m.account_holder_key
    inner join dbt.mmbr_loan_product_mapping mp 
        on m.loan_name = mp.loan_name 
       and mp.product = 'consumer_credit'
    left join private.californium_credit_score_audit_log c 
        on c.user_id = mum.user_id 
       and c.requested_on <= m.creation_date
    left join rating_map rm
        on c.rating = rm.rating
where c.rating <> 'UNKNOWN'
)
select
    l.user_id,
    l.rating as latest_rating,
    l.requested_on as latest_requested_on,
    w.rating as worst_rating,
    w.requested_on as worst_requested_on,
    l.purpose,
    l.creation_date
from scored l
join scored w
  on l.user_id = w.user_id
 where l.rn_latest = 1
   and w.rn_worst = 1

"""

schufa_score_data = pd.read_sql_query(query, conn)
et = time.time()
elapsed_time = et - st
print('Execution time:', elapsed_time/60, 'minutes')

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/1887570812.py:67: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  schufa_score_data = pd.read_sql_query(query, conn)


Execution time: 0.3046495676040649 minutes


In [79]:
schufa_score_data

user_id latest_rating latest_requested_on  \
0      009ac367-2d15-4ead-8cb8-e0744165e10d             E          2017-02-18   
1      00dc9949-ea7c-4bbd-9ad4-ba429733197d             D          2024-10-26   
2      00e7584a-966a-41c6-a9af-91a5f01bb26b             M          2022-10-07   
3      00f299ea-0832-4ffa-963e-b5e60ae1aafc             C          2024-02-12   
4      027091e7-4af3-4067-9572-63aa6e1e0fe5             E          2025-05-23   
...                                     ...           ...                 ...   
28631  f8c065d0-a2d1-4523-8fb8-a66f82b0ea35             C          2024-02-13   
28632  f8d435b6-8a0a-49f8-afdd-72977b8dc42a             A          2024-06-28   
28633  fa8d59d5-76f1-4876-b2f1-2d6dd5b871da             D          2024-11-13   
28634  fbe11708-0bf1-4796-ab94-106ce34db71a             D          2019-07-15   
28635  ffb3ad5a-9642-4732-bd78-fd3c13a4d7eb             D          2023-02-07   

      worst_rating worst_requested_on    purpose creation_date  
0                F         2016-09-15  OVERDRAFT    2017-02-24  
1                P         2020-12-01   FOLLOWUP    2024-11-04  
2                M         2022-10-07  OVERDRAFT    2025-04-25  
3                M         2021-03-15     CREDIT    2024-02-12  
4                E         2025-05-23    PRODUCT    2025-07-24  
...            ...                ...        ...           ...  
28631            E         2019-10-16     CREDIT    2025-07-22  
28632            I         2016-04-05     CREDIT    2024-06-28  
28633            D         2024-11-13   FOLLOWUP    2025-07-05  
28634            D         2017-11-13  OVERDRAFT    2024-11-29  
28635            G         2018-12-04  OVERDRAFT    2023-02-07  

[28636 rows x 7 columns]

In [80]:
schufa_score_data['creation_date'] = pd.to_datetime(schufa_score_data['creation_date'])

In [81]:
final_v2 = final_v1.merge(schufa_score_data, on=['user_id'], how='left')

In [82]:
bins = [0, 2000, 5000, 10000, 15000, 20000, float('inf')]
labels = ["<=2000", "2001-5000", "5001-10000", "10001-15000", "15001-20000", ">20000"]

# Apply bucketing
final_v2["loan_amount_bucket"] = pd.cut(final_v2["loan_amount"], bins=bins, labels=labels, right=True)

In [83]:
final_v2[final_v2['gambled_6m_before']==True].head(20)

user_id                       encoded_key  \
0   83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1   682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2   c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
4   1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
5   1ad2a561-e035-4d35-8256-3c9209887b8a  8a868e5a9442919501944b4754881dca   
6   5fe5414f-2b00-4261-9b22-0977631a04a2  8a868ea69389f73d0193db7f962a1acc   
7   40c9007b-5265-48e0-b9eb-6b1e28f99441  8a868f1d9145954701914fe4fd980032   
8   578df97f-f54d-4325-b41d-15476e196151  8a868eeb8ccb6a17018cd4393d8b5af4   
9   578df97f-f54d-4325-b41d-15476e196151  8a868f46938a01490193d487bcef4a4b   
10  ed944f2e-ba2a-4b26-a1c9-77bbf1d59bbb  8a868f4e8dec6710018dee78336b56f5   
11  18e35c65-ef71-440b-9279-5d6768f78528  8a868e15917522a70191fc3f3a8b06a7   
13  5837e275-e625-45d8-a130-c2910681340b  8a868ed9936f6bf501937ee924fe38de   
14  50265293-e3ee-4662-b4bb-0644b8f0009a  8a868e2a946bbfb00194734729e00c22   
15  20cd6d14-2b86-4225-8b58-9f52e2119787  8a868e2b9236251e01926bb1de8223aa   
16  225329f1-250f-4130-91a1-82c0c1fad326  8a868f0c949502e90194b6b18cf47daf   
17  793e07a7-b2c5-4a78-99f0-c3f0df47bd6f  8a868f478eae3184018eb3b9104143f6   
18  e76fac02-2d97-49ba-abfb-f22245cd9277  8a868e3991751c10019197d2e1d65a51   
19  e67397bd-cf5d-4898-9148-bd9211a420f8  8a868ea59389ee1501941b77730b328e   
21  57e127cf-64aa-4392-ad5f-d75a4e1c40de  8a868ec1936f6afd019386e737a83a28   
22  32347227-80b4-4c53-9492-acec113562f8  8a868f46938a01490193fdaea11a4f85   

   creation_date_x  loan_amount     first_gamble_before_cd  \
0       2024-06-24      10000.0 2023-09-04 17:14:07.553852   
1       2024-10-01      25000.0 2021-03-23 19:18:45.387495   
2       2024-11-20       5200.0 2021-01-22 17:09:27.664615   
4       2025-01-08       2000.0 2023-12-28 17:35:34.234032   
5       2025-01-09      10000.0 2024-12-02 19:19:27.224137   
6       2024-12-18       2500.0 2023-03-29 16:33:59.541813   
7       2024-08-14       1000.0 2022-10-13 20:37:16.243252   
8       2024-01-04      10000.0 2022-07-19 16:14:52.645871   
9       2024-12-17      10000.0 2022-07-19 16:14:52.645871   
10      2024-02-28       5000.0 2019-01-08 17:16:06.999592   
11      2024-09-16       1000.0 2023-03-26 22:15:02.454553   
13      2024-11-30       3400.0 2020-12-04 09:16:19.789183   
14      2025-01-17      10000.0 2024-05-10 15:43:40.838762   
15      2024-10-08       1000.0 2024-03-17 21:59:15.431344   
16      2025-01-30       4000.0 2024-01-14 18:20:46.327261   
17      2024-04-06       4000.0 2024-01-03 17:01:24.118593   
18      2024-08-28       2500.0 2018-11-22 17:09:24.017039   
19      2024-12-31      13000.0 2018-07-11 23:24:58.071298   
21      2024-12-02       8000.0 2024-11-19 17:56:41.196967   
22      2024-12-25      25000.0 2023-03-23 17:10:45.203501   

        last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
0  2024-01-19 17:05:25.602680                       7                151.40   
1  2024-04-15 23:48:37.539253                       9               1234.69   
2  2024-11-05 18:45:19.001744                     189                722.04   
4  2025-01-07 17:36:04.653845                     115               1362.98   
5  2024-12-10 18:32:38.750347                       2                 19.60   
6  2024-10-28 17:20:03.127990                      40                254.40   
7  2024-08-13 16:14:52.967076                      64                415.60   
8  2023-12-19 18:11:00.494452                      45                125.26   
9  2024-12-10 18:22:35.906937                      89                237.86   
10 2024-01-03 18:34:13.046738                      26                303.51   
11 2024-09-10 19:45:47.915698                      64               1033.84   
13 2024-11-26 18:19:00.375456                      17                237.80   
14 2024-08-02 20:21:41.900706                      11           

In [76]:
st = time.time()

query = f"""

with credit_score as (
select distinct 
m.encoded_key 
, m.creation_date 
, case
                when cs.criteria = 'N26_CREDIT_SCORE'
                then
                    json_extract_path_text(
                        json_extract_array_element_text('[' || cs.raw_value || ']', 0), 'score'
                    )
            end::smallint as score
from etl_reporting.consumercredit_credit_decision dc 
inner join etl_reporting.consumercredit_credit_decision_criteria cs on cs.decision_id = dc.id and cs.criteria in ('N26_CREDIT_SCORE')
inner join consumercredit_credit_draft cd on cd.id = dc.loan_id
inner join mmbr_loan_account m on m.id = cd.loan_id
)

, repayment_capacity as (
select distinct 
m.encoded_key 
, m.creation_date 
, case
                when cs.criteria = 'HAS_ENOUGH_REPAYMENT_CAPACITY'
                then
                    json_extract_path_text(
                        json_extract_array_element_text('[' || cs.raw_value || ']', 0), 'amount'
                    )
            end::float as repcapacity
from etl_reporting.consumercredit_credit_decision dc 
inner join etl_reporting.consumercredit_credit_decision_criteria cs on cs.decision_id = dc.id and cs.criteria in ('HAS_ENOUGH_REPAYMENT_CAPACITY')
inner join consumercredit_credit_draft cd on cd.id = dc.loan_id
inner join mmbr_loan_account m on m.id = cd.loan_id
)


select
c.encoded_key,
c.creation_date as score_creation_date,
r.creation_date as repcap_creation_date,
case when coalesce(a.rating_class, c.score) <= 7 then '1. 1_7'
     when coalesce(a.rating_class, c.score) = 8 then '2. 8' 
     when coalesce(a.rating_class, c.score) = 9 then '3. 9' 
     when coalesce(a.rating_class, c.score) = 10 then '4. 10'
	 when coalesce(a.rating_class, c.score) = 11 then '5. 11'
	 when coalesce(a.rating_class, c.score) = 12 then '6. 12'
	 when coalesce(a.rating_class, c.score) > 12 then '7. 12+'
     end as supermodel_score
, case when r.repcapacity is null then '1. No value'
       when r.repcapacity = 0 then '2. 0'
	   when r.repcapacity <= 500 then '3. 1_500'
	   when r.repcapacity <= 1000 then '4. 501_1000'
	   when r.repcapacity <= 2500 then '5. 1001_2500'
	   when r.repcapacity <= 5000 then '6. 2501_5000'
	   when r.repcapacity > 5000 then '7. 5000+' 
	   end as repayment_capacity_amount
from credit_score c
left join etl_reporting.porto_app_scores a on a.instrument_id = c.encoded_key
                                               and a.product_flag = 'CC' 
                                               and a.model_name = 'supermodel-pit-20250225'
                                               and c.creation_date::date = a.credit_creation_date::date 
left join repayment_capacity r on  r.encoded_key=c.encoded_key

"""

other_data = pd.read_sql_query(query, conn)
et = time.time()
elapsed_time = et - st
print('Execution time:', elapsed_time/60, 'minutes')

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_1455/3018270589.py:69: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  other_data = pd.read_sql_query(query, conn)


DatabaseError: Execution failed on sql '

with credit_score as (
select distinct 
m.encoded_key 
, m.creation_date 
, case
                when cs.criteria = 'N26_CREDIT_SCORE'
                then
                    json_extract_path_text(
                        json_extract_array_element_text('[' || cs.raw_value || ']', 0), 'score'
                    )
            end::smallint as score
from etl_reporting.consumercredit_credit_decision dc 
inner join etl_reporting.consumercredit_credit_decision_criteria cs on cs.decision_id = dc.id and cs.criteria in ('N26_CREDIT_SCORE')
inner join consumercredit_credit_draft cd on cd.id = dc.loan_id
inner join mmbr_loan_account m on m.id = cd.loan_id
)

, repayment_capacity as (
select distinct 
m.encoded_key 
, m.creation_date 
, case
                when cs.criteria = 'HAS_ENOUGH_REPAYMENT_CAPACITY'
                then
                    json_extract_path_text(
                        json_extract_array_element_text('[' || cs.raw_value || ']'

In [84]:
other_data = pd.read_csv('score_and_rep_cap.csv')

In [85]:
other_data

encoded_key           score_creation_date  \
0     8a868f46938a0149019392243e514a06     December 4, 2024, 2:47 PM   
1     8a868f439256946801925712b0307e63     October 4, 2024, 10:28 AM   
2     8a868e3c939c63530193aac415490b2f     December 9, 2024, 9:33 AM   
3     8a868e27934b5b2c01934de87bac5f16    November 21, 2024, 8:48 AM   
4     8a868f359389f851019391cbe0d40dc2     December 4, 2024, 1:11 PM   
...                                ...                           ...   
9727  8a868f149389f7420193c10953ac74ea    December 13, 2024, 5:20 PM   
9728  8a868f7c8d5b793b018d6312654d427f     February 1, 2024, 5:09 AM   
9729  8a868f419389ed2a0193c1091d973350    December 13, 2024, 5:20 PM   
9730  8a868f89920c19cb01920f5af3c157b8  September 20, 2024, 12:14 PM   
9731  8a868ea69389f73d0193bf5e38fa69e1    December 13, 2024, 9:34 AM   

     supermodel_score repayment_capacity_amount  
0              1. 1_7                  3. 1_500  
1                3. 9               4. 501_1000  
2              7. 12+                  3. 1_500  
3                2. 8              5. 1001_2500  
4              1. 1_7                  3. 1_500  
...               ...                       ...  
9727           7. 12+              5. 1001_2500  
9728             3. 9                  7. 5000+  
9729           1. 1_7              6. 2501_5000  
9730            4. 10              5. 1001_2500  
9731             3. 9              6. 2501_5000  

[9732 rows x 4 columns]

In [86]:
final_v3 = final_v2.merge(other_data, on='encoded_key', how='left')

In [87]:
final_v3

user_id                       encoded_key  \
0     83ccdb07-f6dc-4307-beb2-fb065833c36d  8a868e079032532001904b8775382b7b   
1     682ae687-9e54-4df2-8011-3621aa102677  8a868eb7924067ac0192497d9868209a   
2     c619ba80-6486-4b02-812c-47e4f6789f23  8a868e56931c67f601934acb758d72d6   
3     6323a6b7-36f4-497b-872c-a81304e63cea  8a868f44910644540191151268e13e19   
4     1955b37f-09b7-414c-a884-a37ad90b3755  8a868ff094429207019444c2730f12c3   
...                                    ...                               ...   
4154  bdf44b3a-28a9-4842-933f-01a723bc2966  8a868e13920c1a78019213c4fc6640a7   
4155  02db6500-6510-455f-ada7-0ef8ee357893  8a868e8a8da7de73018db1ed84261ec9   
4156  9cc34ea9-7ec1-4da3-82ea-7aaa2cf99335  8a868fbc9442919c01944ca291741856   
4157  4cd111bb-c1e6-4332-95f6-0daeba58819b  8a868ed090325339019067d978ae6ca4   
4158  460ffb1b-9cb2-447d-99f8-45901510d9db  8a868f9992fbb45f0193088dfe640a2b   

     creation_date_x  loan_amount     first_gamble_before_cd  \
0         2024-06-24      10000.0 2023-09-04 17:14:07.553852   
1         2024-10-01      25000.0 2021-03-23 19:18:45.387495   
2         2024-11-20       5200.0 2021-01-22 17:09:27.664615   
3         2024-08-02       8000.0                        NaT   
4         2025-01-08       2000.0 2023-12-28 17:35:34.234032   
...              ...          ...                        ...   
4154      2024-09-21       1000.0 2023-03-22 17:36:28.653315   
4155      2024-02-16       8500.0                        NaT   
4156      2025-01-09      17000.0 2023-12-14 11:41:48.934064   
4157      2024-06-30       2400.0                        NaT   
4158      2024-11-07       2500.0                        NaT   

          last_gamble_before_cd  count_gamble_before_cd  sum_gamble_before_cd  \
0    2024-01-19 17:05:25.602680                       7                151.40   
1    2024-04-15 23:48:37.539253                       9               1234.69   
2    2024-11-05 18:45:19.001744                     189                722.04   
3                           NaT                       0                  0.00   
4    2025-01-07 17:36:04.653845                     115               1362.98   
...                         ...                     ...                   ...   
4154 2023-03-22 17:36:28.653315                       1                 13.80   
4155                        NaT                       0                  0.00   
4156 2023-12-14 11:41:48.934064                       1                  2.89   
4157                        NaT                       0                  0.00   
4158                        NaT                       0                  0.00   

      avg_gamble_before_cd      first_gamble_after_cd  \
0                21.628571 2024-07-11 16:18:03.988261   
1               137.187778 2025-01-30 11:29:50.312069   
2                 3.820317 2024-11-26 17:09:15.088452   
3                      NaN 2024-10-03 01:55:17.660475   
4                11.852000 2025-01-14 17:43:23.286632   
...                    ...                        ...   
4154             13.800000                        NaT   
4155                   NaN 2024-04-08 16:38:10.010730   
4156              2.890000                        NaT   
4157                   NaN 2024-10-31 17:18:31.535462   
4158                   NaN 2025-05-03 10:50:05.251278   

           last_gamble_after_cd  count_gamble_after_cd  sum_gamble_after_cd  \
0    2025-07-30 16:42:27.699472                      3                80.30   
1    2025-01-30 11:29:50.312069                      1                89.03   
2    2025-07-04 16:44:51.681319                     12               115.40   
3    2025-08-13 11:13:21.501474                      7               190.00   
4    2025-08-26 16:52:19.528307                     67               793.09   
...                         ...                    ...                  ...   
4154                        NaT                      0                 0.00   
4155 2024-04-08

In [88]:
bins = [0, 50, 60, 140, float('inf')]
labels = ["0-50", "50-60", "60-140", "140+"]

# Apply bucketing
final_v3["avg_gambling_amount_bucket_before_cd"] = pd.cut(final_v3["avg_gamble_before_cd"], bins=bins, labels=labels, right=True, include_lowest=True)

In [89]:
freq_bins = [0, 10, 300, float('inf')]
freq_labels = ["0-10", "10-300", "300+"]

final_v3['gambling_freq_bucket_before_cd'] = pd.cut(final_v3['count_gamble_before_cd'].fillna(0),bins=freq_bins,labels=freq_labels, right=True, include_lowest=True)

In [90]:
group_11_df = final_v3[final_v3['count_gamble_before_cd'] != 0].copy()

# Aggregate sums
agg = (
    group_11_df
    .groupby(['avg_gambling_amount_bucket_before_cd', 'gambling_freq_bucket_before_cd'])
    [['eur_written_off_within_6m', 'loan_amount']]
    .sum()
    .reset_index()
)

# Compute ratio
agg['wo_ratio'] = agg['eur_written_off_within_6m'] / agg['loan_amount']

# Pivot
pivot = agg.pivot(
    index='avg_gambling_amount_bucket_before_cd',
    columns='gambling_freq_bucket_before_cd',
    values='wo_ratio'
).fillna(0)

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/2007629205.py:6: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  .groupby(['avg_gambling_amount_bucket_before_cd', 'gambling_freq_bucket_before_cd'])


In [91]:
pivot

gambling_freq_bucket_before_cd            0-10    10-300      300+
avg_gambling_amount_bucket_before_cd                              
0-50                                  0.007210  0.006155  0.011882
50-60                                 0.062772  0.097239  0.000000
60-140                                0.000000  0.021579  0.049718
140+                                  0.036595  0.002464  0.000000

In [92]:
final_v3[((final_v3['gambled_6m_before'] == True) & (final_v3['worst_rating'].isin(['N','O','P'])))]['loan_amount'].sum()

2501700.0

In [93]:
final_v3[((final_v3['gambled_6m_before'] == True) & (final_v3['worst_rating'].isin(['N','O','P'])))]['eur_written_off_within_6m'].sum()

40933.0

In [94]:
final_v3[((final_v3['gambled_6m_before'] == True) & (final_v3['worst_rating'].isin(['P'])))]['eur_written_off_within_6m'].sum() / final_v3[((final_v3['gambled_6m_before'] == True) & (final_v3['worst_rating'].isin(['P'])))]['loan_amount'].sum()

0.01847666657510918

In [95]:
final_v3.to_csv('gambling_final_v3.csv')

In [96]:
group_11_df = final_v3[final_v3['count_gamble_before_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_11_df,
    index='avg_gambling_amount_bucket_before_cd',
    columns='gambling_freq_bucket_before_cd',
    values='eur_written_off_within_6m',
    aggfunc='sum',
    fill_value=0
)

In [97]:
pivot

gambling_freq_bucket_before_cd           0-10   10-300    300+
avg_gambling_amount_bucket_before_cd                          
0-50                                  66405.0  51327.0  6508.0
50-60                                 20445.0  28102.0     0.0
60-140                                    0.0  15960.0  1939.0
140+                                  39116.0   1032.0     0.0

In [98]:
group_1_df.groupby('supermodel_score')['eur_written_off_within_6m'].sum()

NameError: name 'group_1_df' is not defined

In [ ]:
import itertools
import numpy as np
import pandas as pd
from typing import List, Dict, Tuple, Optional

# -------------------------------------------------------------
# Core utility: evaluate a pair of bin sets and compute metrics
# -------------------------------------------------------------

def _eval_bins(df: pd.DataFrame,
               amount_bins: List[float],
               freq_bins: List[float],
               min_rate: float = 0.035,
               min_exposure: float = 0.0,
               amount_col: str = "avg_gamble_before_cd",
               freq_col: str = "count_gamble_before_cd",
               wo_eur_col: str = "eur_written_off_within_6m",
               exposure_col: str = "loan_amount",
               exclude_zero_freq: bool = True
              ) -> Dict:
    """Evaluate a given (amount_bins, freq_bins) pair.

    Returns a dict with:
      - 'amount_bins', 'freq_bins'
      - 'table' (DataFrame): wo_ratio pivot table
      - 'bucket_detail' (DataFrame): each bucket with wo_ratio, exposure, wo_eur
      - 'selected_buckets' (DataFrame): buckets chosen using threshold constraints
      - aggregate metrics capturing how much exposure and WO€ are covered by the selected buckets
    """
    work = df.copy()
    work[freq_col] = work[freq_col].fillna(0)
    if exclude_zero_freq:
        work = work[work[freq_col] != 0]

    # Label bins
    amount_labels = [f"{amount_bins[i]}-{amount_bins[i+1]}" if np.isfinite(amount_bins[i+1]) else f">={amount_bins[i]}" for i in range(len(amount_bins)-1)]
    freq_labels   = [f"{freq_bins[i]}-{freq_bins[i+1]}" if np.isfinite(freq_bins[i+1]) else f">={freq_bins[i]}" for i in range(len(freq_bins)-1)]

    # Cut
    work["amount_bucket"] = pd.cut(work[amount_col], bins=amount_bins, labels=amount_labels, right=True, include_lowest=True)
    work["freq_bucket"]   = pd.cut(work[freq_col],   bins=freq_bins,   labels=freq_labels,   right=True, include_lowest=True)

    # Aggregate: WO€, Exposure, Count
    grp = (work
           .groupby(["amount_bucket", "freq_bucket"], dropna=False)
           [[wo_eur_col, exposure_col]]
           .sum()
           .rename(columns={wo_eur_col: "wo_eur", exposure_col: "exposure"})
           .reset_index())
    # Add counts for sanity
    cnt = work.groupby(["amount_bucket", "freq_bucket"]).size().rename("n").reset_index()
    grp = grp.merge(cnt, on=["amount_bucket", "freq_bucket"], how="left")

    # wo ratio
    grp["wo_ratio"] = grp["wo_eur"] / grp["exposure"].replace(0, np.nan)

    # Keep a readable pivot (wo_ratio only)
    pivot = (grp.pivot(index="amount_bucket", columns="freq_bucket", values="wo_ratio")
                .sort_index(axis=0)
                .sort_index(axis=1))

    # Selection rule: bucket qualifies if wo_ratio >= min_rate AND exposure >= min_exposure
    qualified = grp[(grp["wo_ratio"] >= min_rate) & (grp["exposure"] >= min_exposure)].copy()

    # Totals
    total_exposure = grp["exposure"].sum()
    total_wo_eur   = grp["wo_eur"].sum()

    sel_exposure = qualified["exposure"].sum()
    sel_wo_eur   = qualified["wo_eur"].sum()

    metrics = {
        "amount_bins": amount_bins,
        "freq_bins": freq_bins,
        "table": pivot,
        "bucket_detail": grp.sort_values(["amount_bucket", "freq_bucket"]).reset_index(drop=True),
        "selected_buckets": qualified.sort_values(["amount_bucket", "freq_bucket"]).reset_index(drop=True),
        # Aggregates
        "selected_bucket_count": int(qualified.shape[0]),
        "selected_exposure": float(sel_exposure),
        "selected_wo_eur": float(sel_wo_eur),
        "selected_avg_wo_ratio": float(sel_wo_eur / sel_exposure) if sel_exposure > 0 else np.nan,
        # Coverage
        "exposure_impact_pct": float(sel_exposure / total_exposure) if total_exposure > 0 else np.nan,
        "wo_capture_pct": float(sel_wo_eur / total_wo_eur) if total_wo_eur > 0 else np.nan,
        # Overall totals for reference
        "total_exposure": float(total_exposure),
        "total_wo_eur": float(total_wo_eur),
    }
    return metrics


# -------------------------------------------------------------
# Candidate generator helpers
# -------------------------------------------------------------

def make_single_split_candidates(values: List[float]) -> List[List[float]]:
    """Given a sorted list of internal edges (e.g., [20,40,60]),
    return [ [0, v, inf] for each v ]."""
    out = []
    for v in values:
        out.append([0.0, float(v), float("inf")])
    return out


def make_multi_split_candidates(values: List[float], max_splits: int = 3) -> List[List[float]]:
    """Generate bin sets of the form [0, e1, e2, ..., inf], using up to max_splits internal edges.
    Example: values=[2,5,10,25,50,100], max_splits=3 could yield [0,2,inf], [0,5,inf], [0,2,5,inf], [0,5,25,inf], etc.
    """
    values = sorted(values)
    candidates = []
    for k in range(1, max_splits+1):
        for combo in itertools.combinations(values, k):
            bins = [0.0] + list(map(float, combo)) + [float("inf")]
            candidates.append(bins)
    return candidates


# -------------------------------------------------------------
# Main optimizer
# -------------------------------------------------------------

def optimize_gambling_splits(
    df: pd.DataFrame,
    amount_candidate_edges: Optional[List[List[float]]] = None,
    freq_candidate_edges: Optional[List[List[float]]] = None,
    *,
    min_rate: float = 0.035,
    min_exposure: float = 0.0,
    max_freq_splits: int = 3,
    max_amount_splits: int = 2,
    freq_edge_pool: Optional[List[float]] = None,
    amount_edge_pool: Optional[List[float]] = None,
    amount_col: str = "avg_gamble_before_cd",
    freq_col: str = "count_gamble_before_cd",
    wo_eur_col: str = "eur_written_off_within_6m",
    exposure_col: str = "loan_amount",
    exclude_zero_freq: bool = True,
    top_k: int = 15
) -> pd.DataFrame:
    """Grid-search both amount and frequency bin sets.

    Ranking logic:
      1) Maximize WO€ captured by qualified buckets (wo_ratio >= min_rate)
      2) For ties, minimize exposure impact (reject rate proxy)
      3) For ties, maximize average wo_ratio within selected buckets

    Returns a DataFrame of top_k configurations with summary metrics.
    """
    # Default candidate generation if none provided
    if amount_candidate_edges is None:
        # Pool defaults — feel free to tailor
        if amount_edge_pool is None:
            amount_edge_pool = [0,10,20,50,60,80,100,140,180,300]
        amount_candidate_edges = make_multi_split_candidates(amount_edge_pool, max_splits=max_amount_splits)

    if freq_candidate_edges is None:
        if freq_edge_pool is None:
            freq_edge_pool = [0,2,5,8,10,20,50,100,150,200,250,300]
        freq_candidate_edges = make_multi_split_candidates(freq_edge_pool, max_splits=max_freq_splits)

    results = []

    for a_bins in amount_candidate_edges:
        for f_bins in freq_candidate_edges:
            try:
                met = _eval_bins(
                    df,
                    amount_bins=a_bins,
                    freq_bins=f_bins,
                    min_rate=min_rate,
                    min_exposure=min_exposure,
                    amount_col=amount_col,
                    freq_col=freq_col,
                    wo_eur_col=wo_eur_col,
                    exposure_col=exposure_col,
                    exclude_zero_freq=exclude_zero_freq,
                )
                results.append(met)
            except Exception:
                # Safeguard against pathological binning (e.g., no rows in buckets)
                continue

    if not results:
        return pd.DataFrame()

    # Ranking
    res_df = pd.DataFrame([
        {
            "amount_bins": r["amount_bins"],
            "freq_bins": r["freq_bins"],
            "selected_bucket_count": r["selected_bucket_count"],
            "selected_exposure": r["selected_exposure"],
            "selected_wo_eur": r["selected_wo_eur"],
            "selected_avg_wo_ratio": r["selected_avg_wo_ratio"],
            "exposure_impact_pct": r["exposure_impact_pct"],
            "wo_capture_pct": r["wo_capture_pct"],
            "total_exposure": r["total_exposure"],
            "total_wo_eur": r["total_wo_eur"],
        }
        for r in results
    ])

    res_df = res_df.sort_values(
        by=["selected_wo_eur", "exposure_impact_pct", "selected_avg_wo_ratio"],
        ascending=[False, True, False]
    ).head(top_k).reset_index(drop=True)

    return res_df


# -------------------------------------------------------------
# Convenience: show details of one configuration
# -------------------------------------------------------------

def summarize_configuration(df: pd.DataFrame,
                            amount_bins: List[float],
                            freq_bins: List[float],
                            **kwargs) -> Dict[str, pd.DataFrame]:
    """Return the pivot table and the selected-bucket list for a specific bin set."""
    met = _eval_bins(df, amount_bins=amount_bins, freq_bins=freq_bins, **kwargs)
    return {
        "pivot_wo_ratio": met["table"],
        "bucket_detail": met["bucket_detail"],
        "selected_buckets": met["selected_buckets"],
    }


# -------------------------------------------------------------
# Example usage (uncomment and adapt in your notebook):
# -------------------------------------------------------------
#subset = final_v3[final_v3['gambled_6m_before'] == True].copy()
best = optimize_gambling_splits(final_v3,
                                 min_rate=0.03,
                                 min_exposure=0,
                                 max_amount_splits=3,  # up to 3 buckets for amount
                                 max_freq_splits=3,    # up to 4 buckets for freq
                                 top_k=20)


cfg = best.iloc[0]
piv_detail = summarize_configuration(final_v3,
                                      amount_bins=cfg['amount_bins'],
                                      freq_bins=cfg['freq_bins'],
                                      min_rate=0.03,
                                      min_exposure=0)
piv_detail["pivot_wo_ratio"]
piv_detail["selected_buckets"]  # these are the rule candidates to exclude


/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/1299980439.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  .groupby(["amount_bucket", "freq_bucket"], dropna=False)
/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/1299980439.py:51: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  cnt = work.groupby(["amount_bucket", "freq_bucket"]).size().rename("n").reset_index()
/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_51863/1299980439.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=

In [108]:
cfg

amount_bins              [0.0, 20.0, 60.0, 100.0, inf]
freq_bins                        [0.0, 8.0, 20.0, inf]
selected_bucket_count                                3
selected_exposure                            4352931.0
selected_wo_eur                               137316.0
selected_avg_wo_ratio                         0.031546
exposure_impact_pct                           0.197929
wo_capture_pct                                0.594869
total_exposure                             21992365.21
total_wo_eur                                  230834.0
Name: 0, dtype: object

In [109]:
piv_detail["pivot_wo_ratio"]

freq_bucket     0.0-8.0  8.0-20.0    >=20.0
amount_bucket                              
0.0-20.0       0.001088  0.000000  0.005249
20.0-60.0      0.030050  0.018111  0.018694
60.0-100.0     0.000000  0.000000  0.036446
>=100.0        0.032882  0.000000  0.002787

In [154]:
results_df['details'][3004]

[{'amount_bucket': '58+',
  'freq_bucket': '113+',
  'eur_written_off_within_6m': 26435.0,
  'loan_amount': 290165.0,
  'wo_ratio': 0.09110333775610428}]

In [341]:
from scipy.optimize import differential_evolution

def objective(params):
    X1, Y1, X2, Y2 = params
    return -excluded_writeoff_rate(final_v3, X1, Y1, X2, Y2)  # negative for maximization

bounds = [(10, 200), (1, 200), (10, 200), (1, 200)]
result = differential_evolution(objective, bounds, maxiter=50)
print("Best cutoffs:", result.x)
print("Max writeoff rate:", -result.fun)

Best cutoffs: [142.02316917   4.63756148  23.30948041 196.01854932]
Max writeoff rate: 0.03624576068916901


In [319]:
group_11_df = final_v3[final_v3['count_gamble_before_cd'] != 0].copy()

# Aggregate sums
agg = (
    group_11_df
    .groupby(['gambling_freq_bucket', 'gambling_amount_bucket'])
    [['eur_written_off_within_6m', 'loan_amount']]
    .sum()
    .reset_index()
)

# Compute ratio
agg['wo_ratio'] = agg['eur_written_off_within_6m'] / agg['loan_amount']

# Pivot
pivot = agg.pivot(
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='wo_ratio'
).fillna(0)

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_1455/1394073708.py:6: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  .groupby(['gambling_freq_bucket', 'gambling_amount_bucket'])


In [220]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000     2001+
gambling_freq_bucket                                                    
0-2                     0.007798  0.035734  0.000000  0.000000  0.000000
3-8                     0.004646  0.002239  0.017381  0.089821  0.053748
8-25                    0.000000  0.000000  0.000000  0.024268  0.000000
26-100                  0.000000  0.000000  0.000670  0.010965  0.001457
101+                    0.000000  0.000000  0.000000  0.006280  0.019291

In [ ]:
group_11_df = final_v3[final_v3['count_gamble_before_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_11_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='eur_written_off_within_6m'/'loan_amount',
    aggfunc='mean',
    fill_value=0
)

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_1455/1764219488.py:4: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  agg = group_11_df.groupby(


ValueError: Length of values (24) does not match length of index (25)

In [705]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000     2001+
gambling_freq_bucket                                                    
0-2                     0.009431  0.033407  0.000000  0.000000  0.000000
3-8                     0.004561  0.007564  0.029524  0.048730  0.034757
8-25                    0.000000  0.004239  0.000000  0.015932  0.000000
26-100                  0.000000  0.000000  0.003390  0.008176  0.007699
101+                    0.000000  0.000000  0.000000  0.003512  0.020200

In [948]:
group_111_df = final_v1[final_v1['gambled_6m_before'] == True]

# Create pivot table
pivot = pd.pivot_table(
    group_111_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='profit_eur',
    aggfunc='sum',
    fill_value=0
)

In [949]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000    2001+
gambling_freq_bucket                                                   
0-2                     24276.60  -1219.64   1477.02      0.00   624.76
3-8                     10835.89  29909.58  -4933.71    170.92   600.09
8-25                     1870.14  10646.01  11675.65 -13341.25  1653.59
26-100                      0.00   2559.50  10880.09   5550.40  3149.43
101+                        0.00    358.40    772.04   7028.98  4842.09

In [950]:
group_12_df = final_v1[final_v1['count_gamble_before_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_12_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='revenue_eur',
    aggfunc='sum',
    fill_value=0
)

In [951]:
pivot

gambling_amount_bucket       0-50    51-200   201-600  601-2000      2001+
gambling_freq_bucket                                                      
0-2                     109711.86  34702.54  10191.15   4305.09    1365.04
3-8                      48972.58  97172.63  24811.72  10951.96    4450.50
8-25                      5083.77  49733.84  69363.71  36297.29    9169.09
26-100                     629.76   9010.34  65507.98  90887.48   33776.33
101+                         0.00    763.42   9640.36  70147.53  168336.29

In [952]:
group_122_df = final_v1[final_v1['count_gamble_before_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_122_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='eur_written_off_within_6m',
    aggfunc='sum',
    fill_value=0
)

In [953]:
pivot

gambling_amount_bucket     0-50   51-200  201-600  601-2000    2001+
gambling_freq_bucket                                                
0-2                     20595.0  32505.0      0.0       0.0      0.0
3-8                      5177.0   4787.0  10312.0   24638.0   7299.0
8-25                        0.0      0.0      0.0   18122.0      0.0
26-100                      0.0      0.0   1891.0   21634.0   1024.0
101+                        0.0      0.0      0.0   10396.0  72454.0

In [954]:
group_1222_df = final_v1[final_v1['count_gamble_before_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_1222_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='profit_eur',
    aggfunc='sum',
    fill_value=0
)

In [955]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000     2001+
gambling_freq_bucket                                                    
0-2                     89116.86   2197.54  10191.15   4305.09   1365.04
3-8                     43795.58  92385.63  14499.72 -13686.04  -2848.50
8-25                     5083.77  49733.84  69363.71  18175.29   9169.09
26-100                    629.76   9010.34  63616.98  69253.48  32752.33
101+                        0.00    763.42   9640.36  59751.53  95882.29

In [956]:
group_21_df = final_v1[final_v1['gambled_6m_after'] == True]

# Create pivot table
pivot = pd.pivot_table(
    group_21_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='revenue_eur',
    aggfunc='sum',
    fill_value=0
)

In [957]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000      2001+
gambling_freq_bucket                                                     
0-2                     41670.27  12726.91   3865.82    910.80       0.00
3-8                     24438.10  48409.49  13511.33   6281.80    4874.93
8-25                     1643.99  39523.12  49544.99  24126.66    5412.89
26-100                      0.00   8361.39  58296.70  76980.90   25033.95
101+                        0.00    763.42   7948.64  66038.92  156189.54

In [958]:
group_211_df = final_v1[final_v1['gambled_6m_after'] == True]

# Create pivot table
pivot = pd.pivot_table(
    group_211_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='eur_written_off_within_6m',
    aggfunc='sum',
    fill_value=0
)

In [959]:
pivot

gambling_amount_bucket    0-50  51-200  201-600  601-2000    2001+
gambling_freq_bucket                                              
0-2                     4066.0     0.0      0.0    4666.0      0.0
3-8                        0.0  4787.0      0.0       0.0   7299.0
8-25                       0.0     0.0      0.0       0.0      0.0
26-100                     0.0     0.0    901.0   21634.0      0.0
101+                       0.0     0.0      0.0       0.0  71422.0

In [960]:
group_2111_df = final_v1[final_v1['gambled_6m_after'] == True]

# Create pivot table
pivot = pd.pivot_table(
    group_2111_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='profit_eur',
    aggfunc='sum',
    fill_value=0
)

In [961]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000     2001+
gambling_freq_bucket                                                    
0-2                     37604.27  12726.91   3865.82  -3755.20      0.00
3-8                     24438.10  43622.49  13511.33   6281.80  -2424.07
8-25                     1643.99  39523.12  49544.99  24126.66   5412.89
26-100                      0.00   8361.39  57395.70  55346.90  25033.95
101+                        0.00    763.42   7948.64  66038.92  84767.54

In [962]:
final_v1['eur_written_off_within_6m'].sum()

239566.0

In [963]:
group_1_df = final_v1[final_v1['count_gamble_after_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_1_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='revenue_eur',
    aggfunc='sum',
    fill_value=0
)

In [964]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000      2001+
gambling_freq_bucket                                                     
0-2                     68068.08  20482.66   4259.82   1734.49     454.21
3-8                     36560.34  67954.51  18514.79  10620.96    5200.51
8-25                     2139.93  46304.15  60370.16  29499.27    6198.10
26-100                      0.00   9450.22  61080.00  83397.94   26642.21
101+                        0.00    763.42   8540.80  66842.46  160235.23

In [965]:
group_11_df = final_v1[final_v1['count_gamble_after_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_11_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='eur_written_off_within_6m',
    aggfunc='sum',
    fill_value=0
)

In [966]:
pivot

gambling_amount_bucket    0-50  51-200  201-600  601-2000    2001+
gambling_freq_bucket                                              
0-2                     4066.0     0.0      0.0    4666.0      0.0
3-8                        0.0  4787.0      0.0       0.0   7299.0
8-25                       0.0     0.0      0.0       0.0      0.0
26-100                     0.0     0.0    901.0   21634.0      0.0
101+                       0.0     0.0      0.0       0.0  71422.0

In [967]:
group_111_df = final_v1[final_v1['count_gamble_after_cd'] != 0]

# Create pivot table
pivot = pd.pivot_table(
    group_111_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='profit_eur',
    aggfunc='sum',
    fill_value=0
)

In [968]:
pivot

gambling_amount_bucket      0-50    51-200   201-600  601-2000     2001+
gambling_freq_bucket                                                    
0-2                     64002.08  20482.66   4259.82  -2931.51    454.21
3-8                     36560.34  63167.51  18514.79  10620.96  -2098.49
8-25                     2139.93  46304.15  60370.16  29499.27   6198.10
26-100                      0.00   9450.22  60179.00  61763.94  26642.21
101+                        0.00    763.42   8540.80  66842.46  88813.23

In [235]:
group_2_df = final_v1[final_v1['group'] == 'group_2']

# Create pivot table
pivot = pd.pivot_table(
    group_2_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='revenue_eur',
    aggfunc='sum',
    fill_value=0
)

In [236]:
pivot

gambling_amount_bucket       0-50    51-200   201-600  601-2000      2001+
gambling_freq_bucket                                                      
0-2                     151880.67  49891.04  17324.95   6675.39    2739.10
3-8                      57097.65  92614.97  28650.59  16184.62    7454.31
8-25                      3566.95  53866.73  79664.74  36047.98    7878.40
26-100                     629.76   7670.20  60779.83  86958.45   32134.03
101+                         0.00    405.02  10169.55  65786.23  171462.54

In [237]:
group_22_df = final_v1[final_v1['group'] == 'group_2']

# Create pivot table
pivot = pd.pivot_table(
    group_22_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='eur_written_off_within_6m',
    aggfunc='sum',
    fill_value=0
)

In [238]:
pivot

gambling_amount_bucket     0-50   51-200  201-600  601-2000    2001+
gambling_freq_bucket                                                
0-2                     19223.0  22778.0      0.0    4666.0      0.0
3-8                         0.0   4787.0      0.0   22543.0   7299.0
8-25                        0.0      0.0      0.0       0.0      0.0
26-100                      0.0      0.0    990.0    1882.0   1024.0
101+                        0.0      0.0      0.0   10396.0  47561.0

In [239]:
group_222_df = final_v1[final_v1['group'] == 'group_2']

# Create pivot table
pivot = pd.pivot_table(
    group_222_df,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='profit_eur',
    aggfunc='sum',
    fill_value=0
)

In [240]:
pivot

gambling_amount_bucket       0-50    51-200   201-600  601-2000      2001+
gambling_freq_bucket                                                      
0-2                     132657.67  27113.04  17324.95   2009.39    2739.10
3-8                      57097.65  87827.97  28650.59  -6358.38     155.31
8-25                      3566.95  53866.73  79664.74  36047.98    7878.40
26-100                     629.76   7670.20  59789.83  85076.45   31110.03
101+                         0.00    405.02  10169.55  55390.23  123901.54

In [175]:
pivot = pd.pivot_table(
    final_v1,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='eur_written_off_within_6m',
    aggfunc='sum',
    fill_value=0
)

In [176]:
pivot

gambling_amount_bucket     0-50   51-200  201-600  601-2000    2001+
gambling_freq_bucket                                                
0-2                     19223.0  32505.0      0.0    4666.0      0.0
3-8                         0.0   4787.0  10312.0   24638.0   7299.0
8-25                        0.0      0.0      0.0    7810.0      0.0
26-100                      0.0      0.0    990.0    1882.0   1024.0
101+                        0.0      0.0      0.0   10396.0  47561.0

In [177]:
pivot = pd.pivot_table(
    final_v1,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='revenue_eur',
    aggfunc='sum',
    fill_value=0
)

In [178]:
pivot

gambling_amount_bucket       0-50     51-200   201-600  601-2000      2001+
gambling_freq_bucket                                                       
0-2                     178228.17   59689.39  19505.40   6675.39    3363.86
3-8                      67933.54  123492.58  33936.15  18196.40    8054.40
8-25                      5437.09   65739.71  93403.92  40965.04    9531.99
26-100                     629.76    9704.92  72084.81  95014.69   35283.46
101+                         0.00     763.42  10941.59  72698.09  176686.55

In [241]:
pivot = pd.pivot_table(
    final_v1,
    index='gambling_freq_bucket',
    columns='gambling_amount_bucket',
    values='profit_eur',
    aggfunc='sum',
    fill_value=0
)

In [242]:
pivot

gambling_amount_bucket       0-50     51-200   201-600  601-2000      2001+
gambling_freq_bucket                                                       
0-2                     159005.17   27184.39  19505.40   2009.39    3363.86
3-8                      67933.54  118705.58  23624.15  -6441.60     755.40
8-25                      5437.09   65739.71  93403.92  33155.04    9531.99
26-100                     629.76    9704.92  71094.81  93132.69   34259.46
101+                         0.00     763.42  10941.59  62302.09  129125.55

In [247]:
credits = data[['user_id', 'reason', 'credit_creation_date']].drop_duplicates()

KeyError: "['reason', 'credit_creation_date'] not in index"

In [248]:
#data[data['user_id']=='001c1970-cfa3-44ec-8e71-58c423f115b5']

In [146]:
df_pre = data[data['created'] < data['credit_creation_date']]

In [147]:
df_pre['transaction_amount'] = df_pre['transaction_amount'].abs()

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_39913/2544700287.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_pre['transaction_amount'] = df_pre['transaction_amount'].abs()


In [148]:
df_pre[((df_pre['user_id']=='ffe90cef-abe4-4357-a8b1-a28fecd086a6')&(df_pre['transaction_id']=='8a868ec39581db65019595f981665d4d'))]

Empty DataFrame
Columns: [user_id, transaction_id, credit_creation_date, eur_written_off, write_off_dt, reason, closure_type, transaction_amount, transaction_id_g, created]
Index: []

In [149]:
df_pre['reason'].unique()

array(['TBIL', 'Credit', 'Arranged Overdraft'], dtype=object)

In [151]:
df_pre

user_id  \
0       bef258fb-423b-4b2b-b56c-c0a94e223435   
2       43529338-4b3a-44ea-be58-c833cbb92977   
3       43529338-4b3a-44ea-be58-c833cbb92977   
4       43529338-4b3a-44ea-be58-c833cbb92977   
5       43529338-4b3a-44ea-be58-c833cbb92977   
...                                      ...   
854981  d9c4c98a-29cf-4661-9061-969073a779db   
854982  d9c4c98a-29cf-4661-9061-969073a779db   
854983  d9c4c98a-29cf-4661-9061-969073a779db   
854984  d9c4c98a-29cf-4661-9061-969073a779db   
854985  d9c4c98a-29cf-4661-9061-969073a779db   

                          transaction_id credit_creation_date  \
0       8a868e4690dfec170190f7a238dc40ca  2024-07-28 04:38:42   
2       8a868e318dec674d018df4b7dc396a68  2024-02-29 11:55:06   
3       8a868f308dec61ff018df4b0e1d255dd  2024-02-29 11:47:29   
4       8a868f4e8dec6710018df4abbfe70aee  2024-02-29 11:41:54   
5       8a868e318dec674d018df4c8f23a265c  2024-02-29 12:13:46   
...                                  ...                  ...   
854981  8a868f46938a01490193d94e789c377b  2024-12-18 10:26:58   
854982  8a868e15917522a70192092fce976ef7  2024-09-19 07:29:41   
854983  8a868e0a9389ee160193e36fce6617e9  2024-12-20 09:39:35   
854984  8a868ede946bbfa5019482a5043923ec  2025-01-20 07:37:20   
854985  8a868ecc95194b8c0195272fd9db75c3  2025-02-21 06:26:43   

        eur_written_off             write_off_dt reason closure_type  \
0                 131.0  2025-01-11 06:20:38.000   TBIL      DUNNING   
2                  29.0  2024-07-13 02:57:40.000   TBIL      DUNNING   
3                  29.0  2024-07-13 02:57:47.000   TBIL      DUNNING   
4                  29.0  2024-07-13 02:57:49.000   TBIL      DUNNING   
5                  20.0  2024-07-13 02:57:52.000   TBIL      DUNNING   
...                 ...                      ...    ...          ...   
854981             35.0  2025-07-01 07:21:17.000   TBIL      DUNNING   
854982              8.0  2025-07-02 07:18:05.000   TBIL      DUNNING   
854983             35.0  2025-07-03 07:08:41.000   TBIL      DUNNING   
854984             30.0  2025-07-03 07:10:41.000   TBIL      DUNNING   
854985             22.0  2025-07-04 07:10:33.000   TBIL      DUNNING   

        transaction_amount                      transaction_id_g  \
0                    300.0  20eb426a-73aa-39fb-a311-d0f1c5b7015d   
2                     55.0  d9c7ba6e-ba98-3526-bc74-d112169048cc   
3                     55.0  d9c7ba6e-ba98-3526-bc74-d112169048cc   
4                     55.0  d9c7ba6e-ba98-3526-bc74-d112169048cc   
5                     55.0  d9c7ba6e-ba98-3526-bc74-d112169048cc   
...                    ...                                   ...   
854981                80.0  dc252518-62d6-32e1-abeb-973f6b407a9a   
854982                80.0  dc252518-62d6-32e1-abeb-973f6b407a9a   
854983                80.0  dc252518-62d6-32e1-abeb-973f6b407a9a   
854984                80.0  dc252518-62d6-32e1-abeb-973f6b407a9a   
854985                80.0  dc252518-62d6-32e1-abeb-973f6b407a9a   

                       created  
0      2024-01-30 19:58:42.408  
2      2024-01-25 16:04:05.897  
3      2024-01-25 16:04:05.897  
4      2024-01-25 16:04:05.897  
5      2024-01-25 16:04:05.897  
...                        ...  
854981 2023-06-14 16:48:27.599  
854982 2023-06-14 16:48:27.599  
854983 2023-06-14 16:48:27.599  
854984 2023-06-14 16:48:27.599  
854985 2023-06-14 16:48:27.599  

[575181 rows x 10 columns]

In [170]:
agg_extra = df_pre.groupby(['user_id', 'transaction_id', 'reason', 'credit_creation_date', 'eur_written_off']).agg(
    n_transactions = ('transaction_id_g', 'nunique'),
    total_amount = ('transaction_amount', 'sum'),
    avg_amount = ('transaction_amount', 'mean'),
    last_gamble = ('created', 'max'),
    first_gamble = ('created', 'min')
).reset_index()

In [171]:
agg_extra['reason'].unique()

array(['TBIL', 'Credit'], dtype=object)

In [172]:
pcf_data = pd.read_csv('PCF.csv', sep=';')

In [173]:
pcf_data.columns = ['user_id', 'transaction_id', 'reason', 'write_off_dt',
       'eur_written_off', 'loan_amount', 'due_date']

In [174]:
pcf_gambling = pd.merge(agg_extra, pcf_data, on=['user_id', 'transaction_id'])

In [175]:
pcf_gambling['n_instruments'] = pcf_gambling.groupby('user_id')['transaction_id'].transform('nunique')

In [176]:
pcf_gambling = pcf_gambling.sort_values(['user_id', 'credit_creation_date'])
pcf_gambling['n_instruments_present'] = pcf_gambling.groupby('user_id').cumcount() + 1

In [177]:
pcf_gambling

user_id                    transaction_id  \
2     001c1970-cfa3-44ec-8e71-58c423f115b5  8a868f568e521ece018e5552323e1f58   
3     001c1970-cfa3-44ec-8e71-58c423f115b5  8a868f778e5610f2018e562c670c7945   
1     001c1970-cfa3-44ec-8e71-58c423f115b5  8a868edd8e448f45018e562f0e3506c9   
0     001c1970-cfa3-44ec-8e71-58c423f115b5  8a868ec98e82126b018e8b44e20f6a1f   
4     00756cc7-c4eb-4a56-9eb6-807157efa5cc  8a868e15917522a70191c1550cf0142a   
...                                    ...                               ...   
2228  fdb5670b-7158-47af-be45-b89d377f2ce7  8a868fab929c3fc20192a91a7da67f77   
2219  fdb5670b-7158-47af-be45-b89d377f2ce7  8a868e65929c47570192ba1ab7f00bf4   
2230  fe0b3479-782f-4ed7-bf4b-bfed59d1efc9  8a868ff78e821279018e9a4bbc153000   
2231  feb15262-22bc-4d0c-9264-477ef59a268e  8a868e0f8cedc822018cefe9543615fc   
2232  ffcd5ef7-9625-4dee-a53e-f6adc5a29f2a  8a868fd78d4517ec018d4b9e06ac7f60   

     reason_x credit_creation_date  eur_written_off_x  n_transactions  \
2        TBIL  2024-03-19 06:07:15               21.0               4   
3        TBIL  2024-03-19 10:05:35               62.0               4   
1        TBIL  2024-03-19 10:08:28               27.0               4   
0        TBIL  2024-03-29 17:32:14               67.0               4   
4        TBIL  2024-09-05 08:37:42              225.0               3   
...       ...                  ...                ...             ...   
2228     TBIL  2024-10-20 08:45:38              102.0              52   
2219     TBIL  2024-10-23 15:59:27               51.0              52   
2230     TBIL  2024-04-01 15:33:58               58.0             130   
2231     TBIL  2024-01-09 20:28:15              126.0              45   
2232     TBIL  2024-01-27 15:51:04              158.0               2   

      total_amount  avg_amount             last_gamble  \
2            38.20    9.550000 2023-11-26 11:52:35.863   
3            38.20    9.550000 2023-11-26 11:52:35.863   
1            38.20    9.550000 2023-11-26 11:52:35.863   
0            38.20    9.550000 2023-11-26 11:52:35.863   
4            56.20   18.733333 2024-07-24 16:49:22.728   
...            ...         ...                     ...   
2228       4431.22   79.128929 2024-07-16 18:51:44.669   
2219       4431.22   79.128929 2024-07-16 18:51:44.669   
2230        706.10    5.431538 2024-03-26 23:22:00.359   
2231       1450.00   32.222222 2024-01-09 20:14:27.464   
2232        100.00   50.000000 2023-12-07 18:22:16.879   

                first_gamble reason_y             write_off_dt  \
2    2023-11-24 14:55:02.005     TBIL  2024-08-02 14:54:06.000   
3    2023-11-24 14:55:02.005     TBIL  2024-08-02 14:55:06.000   
1    2023-11-24 14:55:02.005     TBIL  2024-08-02 14:51:01.000   
0    2023-11-24 14:55:02.005     TBIL  2024-08-12 06:06:35.000   
4    2023-04-01 19:19:18.225     TBIL  2024-12-15 09:00:49.000   
...                      ...      ...                      ...   
2228 2023-04-05 15:07:03.751     TBIL  2025-03-05 05:43:16.000   
2219 2023-04-05 15:07:03.751     TBIL  2025-03-08 05:45:39.000   
2230 2023-03-31 10:04:51.235     TBIL  2024-08-14 07:10:40.000   
2231 2023-09-12 19:16:51.166     TBIL  2024-05-24 02:20:26.000   
2232 2023-12-06 17:49:15.198     TBIL  2024-05-30 14:08:09.000   

      eur_written_off_y  loan_amount                 due_date  n_instruments  \
2                  21.0        20.51  2024-04-19 00:00:00.000              4   
3                  62.0        58.56  2024-04-19 00:00:00.000              4   
1                  27.0        25.55  2024-04-19 00:00:00.000              4   
0                  67.0        63.29  2024-04-29 00:00:00.000              4   
4                 225.0       218.50  2024-10-05 00:00:00.000              2   
...                 ...          ...                      ...            ...   
2228              102.0       100.00  2024-11-20 00:00:00.000             15   
2219               51.0        50.00  2024-11-23 00:00:00.000      

In [178]:
pcf_gambling.to_csv('pcf_gambling_instrument_level.csv')

In [179]:
pcf_gambling['user_id'].nunique()

732

In [180]:
agg_df = pcf_gambling.groupby(['user_id', 'reason_x']).agg({
    'eur_written_off_x': 'sum',
    'credit_creation_date': ['min', 'max'],
    'n_instruments': 'max',
    'n_transactions': ['min', 'max'],
    'total_amount': ['min', 'max'],
    'first_gamble': 'min',
    'last_gamble': 'max'
    })

In [181]:
agg_df.columns = ['sum_eur_written_off', 'min_credit_creation_date', 'max_credit_creation_date',
                  'n_instruments', 'min_n_transactions', 'max_n_transactions', 'min_total_amount', 'max_total_amount', 'first_gamble', 'last_gamble']

agg_df = agg_df.reset_index()

In [182]:
agg_df

user_id reason_x  sum_eur_written_off  \
0    001c1970-cfa3-44ec-8e71-58c423f115b5     TBIL                177.0   
1    00756cc7-c4eb-4a56-9eb6-807157efa5cc     TBIL                358.0   
2    019f023f-ec05-475f-96a3-3e8100071e93     TBIL                485.0   
3    01a28b65-3f06-41f3-9cbc-bf6c3f814975     TBIL                205.0   
4    01fb9d58-9196-4151-a8d1-01f2b3e2b2d2     TBIL                212.0   
..                                    ...      ...                  ...   
732  fcd8be88-0ccb-4f65-9d9c-182896ce175a     TBIL               1941.0   
733  fdb5670b-7158-47af-be45-b89d377f2ce7     TBIL               1393.0   
734  fe0b3479-782f-4ed7-bf4b-bfed59d1efc9     TBIL                 58.0   
735  feb15262-22bc-4d0c-9264-477ef59a268e     TBIL                126.0   
736  ffcd5ef7-9625-4dee-a53e-f6adc5a29f2a     TBIL                158.0   

    min_credit_creation_date max_credit_creation_date  n_instruments  \
0        2024-03-19 06:07:15      2024-03-29 17:32:14              4   
1        2024-09-05 08:37:42      2024-09-05 08:38:36              2   
2        2024-09-02 10:45:07      2024-09-02 15:34:23              5   
3        2025-03-06 11:43:28      2025-03-08 19:48:33              4   
4        2024-06-24 07:54:10      2024-06-24 07:54:10              1   
..                       ...                      ...            ...   
732      2024-10-06 10:57:04      2024-10-07 13:20:46             29   
733      2024-09-29 18:45:53      2024-10-23 15:59:27             15   
734      2024-04-01 15:33:58      2024-04-01 15:33:58              1   
735      2024-01-09 20:28:15      2024-01-09 20:28:15              1   
736      2024-01-27 15:51:04      2024-01-27 15:51:04              1   

     min_n_transactions  max_n_transactions  min_total_amount  \
0                     4                   4             38.20   
1                     3                   3             56.20   
2                    20                  20            243.00   
3                    16                  20           1120.02   
4                     3                   3             80.00   
..                  ...                 ...               ...   
732                  16                  16            120.00   
733                  52                  52           4431.22   
734                 130                 130            706.10   
735                  45                  45           1450.00   
736                   2                   2            100.00   

     max_total_amount            first_gamble             last_gamble  
0               38.20 2023-11-24 14:55:02.005 2023-11-26 11:52:35.863  
1               56.20 2023-04-01 19:19:18.225 2024-07-24 16:49:22.728  
2              243.00 2023-06-22 16:04:41.509 2024-04-18 07:26:10.449  
3             1360.02 2023-08-28 18:27:09.535 2025-03-08 12:32:07.735  
4               80.00 2024-06-19 14:55:37.819 2024-06-23 12:36:54.239  
..                ...                     ...                     ...  
732            120.00 2023-03-24 19:07:05.998 2024-08-30 22:04:59.130  
733           4431.22 2023-04-05 15:07:03.751 2024-07-16 18:51:44.669  
734            706.10 2023-03-31 10:04:51.235 2024-03-26 23:22:00.359  
735           1450.00 2023-09-12 19:16:51.166 2024-01-09 20:14:27.464  
736            100.00 2023-12-06 17:49:15.198 2023-12-07 18:22:16.879  

[737 rows x 12 columns]

In [183]:
agg_df.to_csv('pcf_gambling_user_level.csv')

In [8]:
tx_data = pd.read_csv('all_gambling_tx.csv', sep=';')

In [4]:
wo_data = pd.read_csv('writeoff_cc.csv', sep=';')

In [7]:
wo_data['credit_creation_date'].min()

'2017-05-03 15:36:11.000'

In [ ]:
merged = wo_data.merge(tx_data, left_on = ['user_id'], right_on = ['user_id'])

In [10]:
merged

user_id             write_off_dt  \
0     67a13fff-d7fa-4798-910d-7180ef70ddee  2024-05-07 13:16:12.000   
1     67a13fff-d7fa-4798-910d-7180ef70ddee  2024-05-07 13:16:12.000   
2     67a13fff-d7fa-4798-910d-7180ef70ddee  2024-05-07 13:16:12.000   
3     67a13fff-d7fa-4798-910d-7180ef70ddee  2024-05-07 13:16:12.000   
4     67a13fff-d7fa-4798-910d-7180ef70ddee  2024-05-07 13:16:12.000   
...                                    ...                      ...   
6096  acba0d8f-f575-4dbe-a465-dff928a221d7  2025-06-13 12:07:03.000   
6097  acba0d8f-f575-4dbe-a465-dff928a221d7  2025-06-13 12:07:03.000   
6098  acba0d8f-f575-4dbe-a465-dff928a221d7  2025-06-13 12:07:03.000   
6099  acba0d8f-f575-4dbe-a465-dff928a221d7  2025-06-13 12:07:03.000   
6100  acba0d8f-f575-4dbe-a465-dff928a221d7  2025-06-13 12:07:03.000   

                          arrear_dt closure_type  reason reason_details  \
0     2024-01-23 01:00:00.000 +0100      DUNNING  Credit         Credit   
1     2024-01-23 01:00:00.000 +0100      DUNNING  Credit         Credit   
2     2024-01-23 01:00:00.000 +0100      DUNNING  Credit         Credit   
3     2024-01-23 01:00:00.000 +0100      DUNNING  Credit         Credit   
4     2024-01-23 01:00:00.000 +0100      DUNNING  Credit         Credit   
...                             ...          ...     ...            ...   
6096                            NaN          AML  Credit         Credit   
6097                            NaN          AML  Credit         Credit   
6098                            NaN          AML  Credit         Credit   
6099                            NaN          AML  Credit         Credit   
6100                            NaN          AML  Credit         Credit   

     reference_to_original_operation                  transaction_id_x  \
0                             Credit  8a868ea8880c507801880e5131d74978   
1                             Credit  8a868ea8880c507801880e5131d74978   
2                             Credit  8a868ea8880c507801880e5131d74978   
3                             Credit  8a868ea8880c507801880e5131d74978   
4                             Credit  8a868ea8880c507801880e5131d74978   
...                              ...                               ...   
6096                          Credit  8a868ebb75fe03e30175fe29a775067d   
6097                          Credit  8a868ebb75fe03e30175fe29a775067d   
6098                          Credit  8a868ebb75fe03e30175fe29a775067d   
6099                          Credit  8a868ebb75fe03e30175fe29a775067d   
6100                          Credit  8a868ebb75fe03e30175fe29a775067d   

      od_status  od_user rp_phase_1_user  eur_written_off suspicious_closure  \
0           NaN     True            True            541.0              False   
1           NaN     True            True            541.0              False   
2           NaN     True            True            541.0              False   
3           NaN     True            True            541.0              False   
4           NaN     True            True            541.0              False   
...         ...      ...             ...              ...                ...   
6096        NaN    False           False           2500.0              False   
6097        NaN    False           False           2500.0              False   
6098        NaN    False           False           2500.0              False   
6099        NaN    False           False           2500.0              False   
6100        NaN    False           False           2500.0              False   

        missing_closure_on     credit_creation_date            etl_updated_x  \
0     Closures not missing  2023-05-12 04:56:28.000  2025-07-10 04:24:32.000   
1     Closures not missing  2023-05-12 04:56:28.000  2025-07-10 04:24:32.000   
2     Closures not missing  2023-05-12 04:56:28.000  2025-07-10 04:24:32.000   
3     Closures not missing  2023-05-12 04:56:28.000  2025-07-10 04:24:32.000   
4     Closures not missing  202

In [12]:
merged_tx_before_cc = merged[merged['credit_creation_date'] > merged['created']]

In [13]:
merged_tx_before_cc['user_id'].nunique()

68

In [20]:
merged_tx_before_cc['credit_creation_date'].min()

'2023-06-06 16:03:43.000'

In [41]:
gamble_before_cd = merged_tx_before_cc.groupby(['user_id', 'transaction_id_x', 'credit_creation_date']).agg(
    n_transactions = ('transaction_id_y', 'nunique'),
    total_amount = ('transaction_amount', 'sum'),
    avg_amount = ('transaction_amount', 'mean'),
    write_off = ('eur_written_off', 'min'),
    last_gamble = ('created', 'max'),
    first_gamble = ('created', 'min')
).reset_index()

In [42]:
gamble_before_cd['last_gamble'] = pd.to_datetime(gamble_before_cd['last_gamble'], utc=True).dt.tz_localize(None)
gamble_before_cd['credit_creation_date'] = pd.to_datetime(gamble_before_cd['credit_creation_date'], utc=True).dt.tz_localize(None)

In [43]:
gamble_before_cd['last_gamble_month_diff'] = (
    (gamble_before_cd['credit_creation_date'].dt.to_period('M') - 
     gamble_before_cd['last_gamble'].dt.to_period('M')
    ).apply(lambda x: x.n)
)

In [341]:
gamble_before_cd_6M = gamble_before_cd[gamble_before_cd['last_gamble_month_diff']<=6]

In [346]:
gamble_before_cd_6M['total_amount'] = gamble_before_cd_6M['total_amount'].abs()
gamble_before_cd_6M['avg_amount'] = gamble_before_cd_6M['avg_amount'].abs()

/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_39913/3248612784.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gamble_before_cd_6M['total_amount'] = gamble_before_cd_6M['total_amount'].abs()
/var/folders/1f/pct68c2j21dd7jgky0y_thb80000gp/T/ipykernel_39913/3248612784.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gamble_before_cd_6M['avg_amount'] = gamble_before_cd_6M['avg_amount'].abs()


In [349]:
gamble_before_cd_6M['write_off'].sum()

330459.0

In [347]:
gamble_before_cd_6M.to_csv('gamble_before_cd_6M.csv')

In [61]:
late_first_data = pd.read_csv('first_installments_not_paid.csv', sep=';')

In [62]:
late_first_wo = merged_tx_before_cc.merge(late_first_data, left_on = ['transaction_id_x'], right_on = ['parent_account_key'])

In [63]:
other_wo = merged_tx_before_cc[~(merged_tx_before_cc['transaction_id_x'].isin(late_first_wo['parent_account_key']))]

In [64]:
merged_tx_before_cc['user_id'].nunique()

68

In [67]:
other_wo['user_id'].nunique()

58

In [66]:
late_first_wo['user_id'].nunique()

10

In [68]:
late_first_group = late_first_wo.groupby(['user_id', 'transaction_id_x', 'credit_creation_date']).agg(
    n_transactions = ('transaction_id_y', 'nunique'),
    total_amount = ('transaction_amount', 'sum'),
    write_off = ('eur_written_off', 'min'),
    last_gamble = ('created', 'max'),
    first_gamble = ('created', 'min')
).reset_index()

other_group = other_wo.groupby(['user_id', 'transaction_id_x', 'credit_creation_date']).agg(
    n_transactions = ('transaction_id_y', 'nunique'),
    total_amount = ('transaction_amount', 'sum'),
    write_off = ('eur_written_off', 'min'),
    last_gamble = ('created', 'max'),
    first_gamble = ('created', 'min')
).reset_index()

In [69]:
late_first_group['total_amount'] = late_first_group['total_amount'].abs()
other_group['total_amount'] = other_group['total_amount'].abs()

In [70]:
late_first_group['last_gamble'] = pd.to_datetime(late_first_group['last_gamble'], utc=True).dt.tz_localize(None)
late_first_group['credit_creation_date'] = pd.to_datetime(late_first_group['credit_creation_date'], utc=True).dt.tz_localize(None)

other_group['last_gamble'] = pd.to_datetime(other_group['last_gamble'], utc=True).dt.tz_localize(None)
other_group['credit_creation_date'] = pd.to_datetime(other_group['credit_creation_date'], utc=True).dt.tz_localize(None)

In [71]:
late_first_group['last_gamble_month_diff'] = (
    (late_first_group['credit_creation_date'].dt.to_period('M') - 
     late_first_group['last_gamble'].dt.to_period('M')
    ).apply(lambda x: x.n)
)

other_group['last_gamble_month_diff'] = (
    (other_group['credit_creation_date'].dt.to_period('M') - 
     other_group['last_gamble'].dt.to_period('M')
    ).apply(lambda x: x.n)
)

In [72]:
late_first_group.to_csv('gamble_late_first_wo.csv')
other_group.to_csv('gamble_other_wo.csv')

In [73]:
late_first_wo_no_gambling = wo_data[(~(wo_data['transaction_id'].isin(late_first_wo['transaction_id_x'])) & (wo_data['transaction_id'].isin(late_first_data['parent_account_key'])))]

In [75]:
late_first_wo_no_gambling['eur_written_off'].sum()

194159.0

In [76]:
other_wo_no_gambling = wo_data[(~(wo_data['transaction_id'].isin(other_wo['transaction_id_x'])) & ~(wo_data['transaction_id'].isin(late_first_data['parent_account_key'])))]